# Feature Engineering for Short Interest Forecasting

This notebook builds the final feature matrix combining:
- FINRA short interest data
- OHLCV price/volume data
- Options data (implied volatility, put-call ratios)
- News sentiment
- Analyst ratings
- Fundamental data (shares outstanding)

Output: MultiIndex DataFrame with columns (Ticker, FeatureName, Window)

In [26]:
# Project Setup and Imports
import pandas as pd
import numpy as np
import pyarrow.parquet as pq
import json
import requests
import time
import os
from pathlib import Path
from datetime import datetime, timedelta
from typing import Dict, List, Tuple, Optional, Union
import logging
from concurrent.futures import ThreadPoolExecutor, as_completed
from tqdm import tqdm
import warnings
from dotenv import load_dotenv
import glob

warnings.filterwarnings('ignore')
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', 100)

# Set random seed for reproducibility
np.random.seed(42)

# Configure logging
logging.basicConfig(level=logging.INFO, format='%(asctime)s - %(levelname)s - %(message)s')
logger = logging.getLogger(__name__)

print(f"Starting feature engineering at {datetime.now()}")

Starting feature engineering at 2025-09-29 17:44:41.804316


In [27]:
# Constants and Configuration
PROJECT_ROOT = Path('/Users/joshuacroppenstedt/Desktop/Work/JP Morgan/short_interest_prediction')
DATA_DIR = PROJECT_ROOT / 'data'
CACHE_DIR = DATA_DIR / 'cache'
PRICES_DIR = DATA_DIR / 'prices'
FINRA_DIR = DATA_DIR / 'finra_clean'

# Ensure directories exist
for dir_path in [CACHE_DIR, CACHE_DIR / 'alphavantage', CACHE_DIR / 'finnhub', CACHE_DIR / 'eodhd']:
    dir_path.mkdir(parents=True, exist_ok=True)

# Trading day windows (approximations)
WINDOWS = [10, 21, 42, 63, 126, 252]  # 2w, 1m, 2m, 3m, 6m, 12m
WINDOW_NAMES = ['2w', '1m', '2m', '3m', '6m', '12m']
WINDOW_MAPPING = dict(zip(WINDOWS, WINDOW_NAMES))

# Global settings
USE_CACHE = True
MAX_WORKERS = 4  # For parallel API calls
RATE_LIMIT_DELAY = 0.1  # Base delay between API calls

# Generate timestamp for output files
TIMESTAMP = datetime.now().strftime('%Y%m%d_%H%M')

print(f"Configuration:")
print(f"  - Project root: {PROJECT_ROOT}")
print(f"  - Windows: {WINDOWS}")
print(f"  - Use cache: {USE_CACHE}")
print(f"  - Timestamp: {TIMESTAMP}")

Configuration:
  - Project root: /Users/joshuacroppenstedt/Desktop/Work/JP Morgan/short_interest_prediction
  - Windows: [10, 21, 42, 63, 126, 252]
  - Use cache: True
  - Timestamp: 20250929_1744


In [28]:
# Load API Keys
load_dotenv(PROJECT_ROOT / 'notebooks' / '.env')

API_KEYS = {
    'alphavantage': os.getenv('ALPHAVANTAGE_API_KEY'),
    'finnhub': os.getenv('FINNHUB_API_KEY'),
    'eodhd': os.getenv('EODHD_API_KEY')
}

# Verify keys are loaded (don't print actual keys)
missing_keys = [k for k, v in API_KEYS.items() if not v]
if missing_keys:
    logger.warning(f"Missing API keys: {missing_keys}")
else:
    logger.info("All API keys loaded successfully")

print(f"API keys status: {[k + ('✓' if v else '✗') for k, v in API_KEYS.items()]}")

2025-09-29 17:44:43,175 - INFO - All API keys loaded successfully


API keys status: ['alphavantage✓', 'finnhub✓', 'eodhd✓']


In [29]:
# Load unified price data to get ticker universe
print("Loading unified price data...")

# Find the most recent unified price data file
unified_files = list(PRICES_DIR.glob("unified_price_data_*.parquet"))
if not unified_files:
    raise FileNotFoundError("No unified price data files found. Please run the price cleaning notebook first.")

# Use the most recent file
unified_file = max(unified_files, key=lambda x: x.stat().st_mtime)
print(f"Loading: {unified_file.name}")

# Load the unified price data
unified_price_data = pd.read_parquet(unified_file)
print(f"Unified price data shape: {unified_price_data.shape}")
print(f"Date range: {unified_price_data.index.min()} to {unified_price_data.index.max()}")

# Extract ticker list
if isinstance(unified_price_data.columns, pd.MultiIndex):
    tickers = sorted(unified_price_data.columns.get_level_values(0).unique().tolist())
else:
    raise ValueError("Expected MultiIndex columns in unified price data")

print(f"Total tickers: {len(tickers)}")
print(f"Sample tickers: {tickers[:10]}")

# Store date range for feature alignment
feature_start_date = unified_price_data.index.min()
feature_end_date = unified_price_data.index.max()
print(f"Feature date range: {feature_start_date} to {feature_end_date}")

Loading unified price data...
Loading: unified_price_data_20250929_174321.parquet
Unified price data shape: (2146, 24564)
Date range: 2016-12-29 00:00:00 to 2025-07-15 00:00:00
Total tickers: 4094
Sample tickers: ['A', 'AA', 'AAGIY', 'AAIGF', 'AAL', 'AAME', 'AAOI', 'AAON', 'AAP', 'AAPL']
Feature date range: 2016-12-29 00:00:00 to 2025-07-15 00:00:00
Unified price data shape: (2146, 24564)
Date range: 2016-12-29 00:00:00 to 2025-07-15 00:00:00
Total tickers: 4094
Sample tickers: ['A', 'AA', 'AAGIY', 'AAIGF', 'AAL', 'AAME', 'AAOI', 'AAON', 'AAP', 'AAPL']
Feature date range: 2016-12-29 00:00:00 to 2025-07-15 00:00:00


In [42]:
# Shares Outstanding Feature Engineering from Alpha Vantage
def get_shares_outstanding_alphavantage(ticker: str, api_key: str) -> Optional[pd.DataFrame]:
    """
    Fetch quarterly shares outstanding data from Alpha Vantage SHARES_OUTSTANDING endpoint.
    
    Args:
        ticker: Stock ticker symbol
        api_key: Alpha Vantage API key
        
    Returns:
        DataFrame with quarterly shares outstanding time series or None if failed
    """
    cache_file = CACHE_DIR / 'alphavantage' / f"{ticker}_shares_outstanding.json"
    
    # Check cache first
    if USE_CACHE and cache_file.exists():
        try:
            with open(cache_file, 'r') as f:
                data = json.load(f)
            if 'data' in data and data['data']:
                return parse_shares_outstanding_data(data, ticker)
        except Exception as e:
            logger.warning(f"Cache read failed for {ticker}: {e}")
    
    # Fetch from API using dedicated SHARES_OUTSTANDING endpoint
    url = "https://www.alphavantage.co/query"
    params = {
        'function': 'SHARES_OUTSTANDING',
        'symbol': ticker,
        'apikey': api_key
    }
    
    try:
        time.sleep(RATE_LIMIT_DELAY)  # Rate limiting
        response = requests.get(url, params=params, timeout=30)
        response.raise_for_status()
        
        data = response.json()
        
        # Cache the response
        cache_file.parent.mkdir(parents=True, exist_ok=True)
        with open(cache_file, 'w') as f:
            json.dump(data, f)
        
        # Check response structure and status
        if 'status' in data and data['status'] == 'success' and 'data' in data and data['data']:
            return parse_shares_outstanding_data(data, ticker)
        else:
            logger.warning(f"No shares outstanding data for {ticker}: {data.get('status', 'unknown status')}")
            return None
            
    except Exception as e:
        logger.error(f"Error fetching shares outstanding for {ticker}: {e}")
        return None

def parse_shares_outstanding_data(data: dict, ticker: str) -> Optional[pd.DataFrame]:
    """Parse shares outstanding from Alpha Vantage SHARES_OUTSTANDING endpoint data."""
    try:
        quarterly_data = data['data']  # Changed from 'quarterlyData' to 'data'
        if not quarterly_data:
            return None
        
        records = []
        for quarter_data in quarterly_data:
            date_str = quarter_data.get('date')
            
            # Get both diluted and basic shares outstanding with correct field names
            diluted_shares = quarter_data.get('shares_outstanding_diluted')
            basic_shares = quarter_data.get('shares_outstanding_basic')
            
            # Prefer diluted shares, fallback to basic shares
            shares_value = None
            if diluted_shares and diluted_shares != 'None':
                try:
                    shares_value = float(diluted_shares)
                except (ValueError, TypeError):
                    pass
            
            if shares_value is None and basic_shares and basic_shares != 'None':
                try:
                    shares_value = float(basic_shares)
                except (ValueError, TypeError):
                    pass
            
            if date_str and shares_value:
                records.append({
                    'date': pd.to_datetime(date_str),
                    'shares_outstanding': shares_value,
                    'ticker': ticker
                })
        
        if records:
            df = pd.DataFrame(records)
            df = df.sort_values('date')
            logger.info(f"Retrieved {len(df)} quarterly shares records for {ticker}")
            return df
        else:
            logger.warning(f"No valid shares outstanding data found for {ticker}")
            return None
            
    except Exception as e:
        logger.error(f"Error parsing shares outstanding data for {ticker}: {e}")
        return None

print("Shares outstanding helper functions defined")

Shares outstanding helper functions defined


In [45]:
# Collect quarterly shares outstanding time series for all tickers
def collect_shares_outstanding_data(tickers: List[str], api_key: str, batch_size: int = 50) -> pd.DataFrame:
    """
    Collect quarterly shares outstanding time series for a list of tickers using SHARES_OUTSTANDING endpoint.
    
    Args:
        tickers: List of stock ticker symbols
        api_key: Alpha Vantage API key
        batch_size: Number of tickers to process before showing progress
        
    Returns:
        DataFrame with quarterly shares outstanding time series for all tickers
    """
    all_shares_data = []
    failed_tickers = []
    
    logger.info(f"Starting quarterly shares outstanding collection for {len(tickers)} tickers")
    logger.info("Using Alpha Vantage SHARES_OUTSTANDING endpoint for complete time series")
    
    for i, ticker in enumerate(tickers):
        try:
            # Get quarterly time series from dedicated SHARES_OUTSTANDING endpoint
            shares_df = get_shares_outstanding_alphavantage(ticker, api_key)
            
            if shares_df is not None and not shares_df.empty:
                # Ensure ticker column is set
                if 'ticker' not in shares_df.columns:
                    shares_df['ticker'] = ticker
                all_shares_data.append(shares_df)
                
                # Log the time series data obtained
                date_range = f"{shares_df['date'].min()} to {shares_df['date'].max()}"
                logger.debug(f"Got {len(shares_df)} quarterly records for {ticker} ({date_range})")
            else:
                failed_tickers.append(ticker)
                logger.debug(f"No quarterly data available for {ticker}")
                
        except Exception as e:
            logger.error(f"Failed to get quarterly shares data for {ticker}: {e}")
            failed_tickers.append(ticker)
        
        # Progress update with more detailed info
        if (i + 1) % batch_size == 0:
            success_rate = ((i + 1 - len(failed_tickers)) / (i + 1)) * 100
            total_records = sum(len(df) for df in all_shares_data) if all_shares_data else 0
            logger.info(f"Progress: {i+1}/{len(tickers)} tickers processed. Success rate: {success_rate:.1f}%. Total quarterly records: {total_records}")
    
    # Combine all quarterly time series data
    if all_shares_data:
        combined_df = pd.concat(all_shares_data, ignore_index=True)
        unique_tickers = combined_df['ticker'].nunique()
        total_records = len(combined_df)
        
        # Calculate average quarters per ticker
        avg_quarters = combined_df.groupby('ticker').size().mean()
        
        logger.info(f"Successfully collected quarterly shares data:")
        logger.info(f"  - Tickers with data: {unique_tickers}")
        logger.info(f"  - Total quarterly records: {total_records}")
        logger.info(f"  - Average quarters per ticker: {avg_quarters:.1f}")
        
        if failed_tickers:
            logger.warning(f"Failed to collect data for {len(failed_tickers)} tickers: {failed_tickers[:10]}...")
        
        return combined_df
    else:
        logger.error("No quarterly shares outstanding data collected")
        return pd.DataFrame()

# Execute the data collection
logger.info("=" * 60)
logger.info("STARTING SHARES OUTSTANDING DATA COLLECTION")
logger.info("=" * 60)

# Get API key
alpha_vantage_key = API_KEYS.get('alphavantage')
if not alpha_vantage_key:
    raise ValueError("Alpha Vantage API key not found")

# Collect data for all tickers
shares_outstanding_df = collect_shares_outstanding_data(
    tickers=tickers,
    api_key=alpha_vantage_key,
    batch_size=50
)

# Display quarterly time series results
if not shares_outstanding_df.empty:
    print(f"\nQuarterly Shares Outstanding Time Series Collection Summary:")
    print(f"- Total tickers with quarterly data: {shares_outstanding_df['ticker'].nunique()}")
    print(f"- Total quarterly records collected: {len(shares_outstanding_df)}")
    print(f"- Date range: {shares_outstanding_df['date'].min()} to {shares_outstanding_df['date'].max()}")
    
    # Calculate time series statistics
    quarters_per_ticker = shares_outstanding_df.groupby('ticker').size()
    print(f"- Average quarters per ticker: {quarters_per_ticker.mean():.1f}")
    print(f"- Max quarters for any ticker: {quarters_per_ticker.max()}")
    print(f"- Min quarters for any ticker: {quarters_per_ticker.min()}")
    
    # Show sample quarterly time series data
    print(f"\nSample quarterly time series data:")
    sample_ticker = shares_outstanding_df['ticker'].iloc[0]
    sample_data = shares_outstanding_df[shares_outstanding_df['ticker'] == sample_ticker].sort_values('date')
    print(f"Example: {sample_ticker} ({len(sample_data)} quarters)")
    print(sample_data[['date', 'shares_outstanding']].head(10))
    
    # Show distribution of quarterly data points per ticker
    print(f"\nQuarterly data points distribution:")
    print(f"- Mean: {quarters_per_ticker.mean():.1f} quarters")
    print(f"- Median: {quarters_per_ticker.median():.1f} quarters")
    print(f"- Min: {quarters_per_ticker.min()} quarters")
    print(f"- Max: {quarters_per_ticker.max()} quarters")
    
    # Show tickers with most complete time series
    top_tickers = quarters_per_ticker.nlargest(5)
    print(f"\nTickers with most quarterly data:")
    for ticker, count in top_tickers.items():
        print(f"  {ticker}: {count} quarters")
else:
    print("No quarterly shares outstanding data collected!")

2025-09-29 18:40:33,313 - INFO - ============================================================
2025-09-29 18:40:33,314 - INFO - STARTING SHARES OUTSTANDING DATA COLLECTION
2025-09-29 18:40:33,314 - INFO - ============================================================
2025-09-29 18:40:33,315 - INFO - Starting quarterly shares outstanding collection for 4094 tickers
2025-09-29 18:40:33,315 - INFO - Using Alpha Vantage SHARES_OUTSTANDING endpoint for complete time series
2025-09-29 18:40:33,314 - INFO - STARTING SHARES OUTSTANDING DATA COLLECTION
2025-09-29 18:40:33,314 - INFO - ============================================================
2025-09-29 18:40:33,315 - INFO - Starting quarterly shares outstanding collection for 4094 tickers
2025-09-29 18:40:33,315 - INFO - Using Alpha Vantage SHARES_OUTSTANDING endpoint for complete time series
2025-09-29 18:40:33,924 - INFO - Retrieved 66 quarterly shares records for A
2025-09-29 18:40:33,924 - INFO - Retrieved 66 quarterly shares records for A



Quarterly Shares Outstanding Time Series Collection Summary:
- Total tickers with quarterly data: 2273
- Total quarterly records collected: 114525
- Date range: 2008-03-28 00:00:00 to 2025-08-24 00:00:00
- Average quarters per ticker: 50.4
- Max quarters for any ticker: 72
- Min quarters for any ticker: 1

Sample quarterly time series data:
Example: A (66 quarters)
        date  shares_outstanding
0 2008-07-31         372000000.0
1 2009-01-31               352.0
2 2009-04-30         344000000.0
3 2009-07-31         345000000.0
4 2010-01-31         354000000.0
5 2010-04-30         354000000.0
6 2010-07-31         352000000.0
7 2010-10-31         356000000.0
8 2011-01-31         355000000.0
9 2011-04-30         355000000.0

Quarterly data points distribution:
- Mean: 50.4 quarters
- Median: 58.0 quarters
- Min: 1 quarters
- Max: 72 quarters

Tickers with most quarterly data:
  HSY: 72 quarters
  LSCC: 70 quarters
  AAPL: 69 quarters
  FCX: 69 quarters
  HAL: 69 quarters


In [46]:
# Analyze shares outstanding data coverage and completeness
print("=" * 60)
print("SHARES OUTSTANDING DATA COVERAGE ANALYSIS")
print("=" * 60)

# Define the key date for analysis (start of FINRA data)
analysis_date = pd.to_datetime('2017-12-29')
current_date = pd.to_datetime('2025-09-29')

print(f"Analysis parameters:")
print(f"- Total tickers in universe: {len(tickers)}")
print(f"- Target date range: {analysis_date} to {current_date}")
print(f"- Analysis date (FINRA start): {analysis_date}")

# 1. Check how many tickers we lost (no data at all)
if not shares_outstanding_df.empty:
    tickers_with_data = set(shares_outstanding_df['ticker'].unique())
    tickers_without_data = set(tickers) - tickers_with_data
    
    print(f"\n📊 DATA AVAILABILITY ANALYSIS:")
    print(f"✅ Tickers with shares outstanding data: {len(tickers_with_data):,}")
    print(f"❌ Tickers lost (no data): {len(tickers_without_data):,}")
    print(f"📈 Data coverage rate: {(len(tickers_with_data) / len(tickers) * 100):.1f}%")
    
    if tickers_without_data:
        print(f"\nSample tickers without data: {list(tickers_without_data)[:10]}")
    
    # 2. Check coverage from before 2017-12-29 until now
    print(f"\n📅 HISTORICAL COVERAGE ANALYSIS (from before {analysis_date.date()}):")
    
    # For each ticker with data, check if it has coverage from before analysis_date
    coverage_stats = []
    
    for ticker in tickers_with_data:
        ticker_data = shares_outstanding_df[shares_outstanding_df['ticker'] == ticker]
        
        # Get date range for this ticker
        min_date = ticker_data['date'].min()
        max_date = ticker_data['date'].max()
        
        # Check if ticker has data from before analysis_date
        has_pre_analysis_data = min_date < analysis_date
        
        # Check if ticker has recent data (within last year)
        has_recent_data = max_date >= (current_date - pd.Timedelta(days=365))
        
        # Check if ticker spans the full period we care about
        full_coverage = has_pre_analysis_data and has_recent_data
        
        coverage_stats.append({
            'ticker': ticker,
            'min_date': min_date,
            'max_date': max_date,
            'quarters': len(ticker_data),
            'has_pre_analysis_data': has_pre_analysis_data,
            'has_recent_data': has_recent_data,
            'full_coverage': full_coverage,
            'date_span_years': (max_date - min_date).days / 365.25
        })
    
    coverage_df = pd.DataFrame(coverage_stats)
    
    # Summary statistics
    tickers_with_pre_analysis = coverage_df['has_pre_analysis_data'].sum()
    tickers_with_recent = coverage_df['has_recent_data'].sum()
    tickers_with_full_coverage = coverage_df['full_coverage'].sum()
    
    print(f"📊 Coverage Statistics:")
    print(f"  Tickers with data before {analysis_date.date()}: {tickers_with_pre_analysis:,} ({tickers_with_pre_analysis/len(tickers_with_data)*100:.1f}%)")
    print(f"  Tickers with recent data (last year): {tickers_with_recent:,} ({tickers_with_recent/len(tickers_with_data)*100:.1f}%)")
    print(f"  Tickers with FULL coverage (pre-2017 to recent): {tickers_with_full_coverage:,} ({tickers_with_full_coverage/len(tickers_with_data)*100:.1f}%)")
    
    # Additional insights
    avg_span = coverage_df['date_span_years'].mean()
    median_quarters = coverage_df['quarters'].median()
    
    print(f"\n📈 Data Quality Metrics:")
    print(f"  Average data span: {avg_span:.1f} years")
    print(f"  Median quarters per ticker: {median_quarters:.0f}")
    print(f"  Tickers with 10+ years of data: {(coverage_df['date_span_years'] >= 10).sum():,}")
    print(f"  Tickers with 50+ quarters: {(coverage_df['quarters'] >= 50).sum():,}")
    
    # Show examples of well-covered tickers
    well_covered = coverage_df[coverage_df['full_coverage']].nlargest(10, 'quarters')
    print(f"\n🏆 Top 10 best-covered tickers (full period coverage):")
    for _, row in well_covered.iterrows():
        print(f"  {row['ticker']}: {row['quarters']:.0f} quarters ({row['min_date'].date()} to {row['max_date'].date()})")
    
    # Show examples of limited coverage
    limited_coverage = coverage_df[~coverage_df['full_coverage']].nsmallest(10, 'quarters')
    if not limited_coverage.empty:
        print(f"\n⚠️  Examples of limited coverage tickers:")
        for _, row in limited_coverage.head(5).iterrows():
            print(f"  {row['ticker']}: {row['quarters']:.0f} quarters ({row['min_date'].date()} to {row['max_date'].date()})")
    
    # Overall assessment for modeling
    print(f"\n🎯 MODELING SUITABILITY ASSESSMENT:")
    usable_for_modeling = coverage_df['full_coverage'].sum()
    print(f"  Tickers suitable for full-period modeling: {usable_for_modeling:,}")
    print(f"  Percentage of original universe: {(usable_for_modeling / len(tickers) * 100):.1f}%")
    print(f"  Percentage of tickers with any data: {(usable_for_modeling / len(tickers_with_data) * 100):.1f}%")
    
else:
    print("❌ No shares outstanding data collected - cannot perform analysis")

SHARES OUTSTANDING DATA COVERAGE ANALYSIS
Analysis parameters:
- Total tickers in universe: 4094
- Target date range: 2017-12-29 00:00:00 to 2025-09-29 00:00:00
- Analysis date (FINRA start): 2017-12-29 00:00:00

📊 DATA AVAILABILITY ANALYSIS:
✅ Tickers with shares outstanding data: 2,273
❌ Tickers lost (no data): 1,821
📈 Data coverage rate: 55.5%

Sample tickers without data: ['PSO', 'EMB', 'PENN', 'UBR', 'XOP', 'GDX', 'SPYG', 'BIB', 'TEI', 'ONEQ']

📅 HISTORICAL COVERAGE ANALYSIS (from before 2017-12-29):
📊 Coverage Statistics:
  Tickers with data before 2017-12-29: 2,043 (89.9%)
  Tickers with recent data (last year): 2,172 (95.6%)
  Tickers with FULL coverage (pre-2017 to recent): 1,978 (87.0%)

📈 Data Quality Metrics:
  Average data span: 13.0 years
  Median quarters per ticker: 58
  Tickers with 10+ years of data: 1,894
  Tickers with 50+ quarters: 1,547

🏆 Top 10 best-covered tickers (full period coverage):
  HSY: 72 quarters (2008-06-29 to 2025-03-30)
  SLB: 69 quarters (2008-06-

In [52]:
# Data Quality Check and Correction
print("=" * 60)
print("DATA QUALITY CHECK AND CORRECTION FOR SHARES OUTSTANDING")
print("=" * 60)

if not shares_outstanding_df.empty:
    # Create a copy for correction
    shares_corrected_df = shares_outstanding_df.copy()
    correction_log = []
    
    print("🔍 Phase 1: Identifying data quality issues...")
    
    # 1. Check for suspiciously small values (likely missing multiplication)
    small_values = shares_corrected_df[shares_corrected_df['shares_outstanding'] < 1000]
    
    if not small_values.empty:
        print(f"⚠️  Found {len(small_values)} records with suspiciously small values (<1000):")
        print(small_values[['ticker', 'date', 'shares_outstanding']].head(10))
        
        # Check specific case mentioned by user
        ticker_a_data = shares_corrected_df[shares_corrected_df['ticker'] == 'A']
        suspicious_a = ticker_a_data[ticker_a_data['shares_outstanding'] < 1000]
        if not suspicious_a.empty:
            print(f"\n🔍 Ticker 'A' suspicious values:")
            print(suspicious_a[['date', 'shares_outstanding']])
    else:
        print("✅ No suspiciously small values found")
    
    # 2. Check for extreme variations within tickers
    print(f"\n📊 Checking for extreme variations within tickers...")
    ticker_stats = shares_corrected_df.groupby('ticker')['shares_outstanding'].agg(['min', 'max', 'std', 'count'])
    ticker_stats['ratio'] = ticker_stats['max'] / ticker_stats['min']
    
    # Find tickers with extreme ratios (>1000x difference)
    extreme_ratios = ticker_stats[ticker_stats['ratio'] > 1000]
    if not extreme_ratios.empty:
        print(f"⚠️  Found {len(extreme_ratios)} tickers with extreme min/max ratios (>1000x):")
        print(extreme_ratios.head())
        
        # Show examples of problematic data
        for ticker in extreme_ratios.head(3).index:
            ticker_data = shares_corrected_df[shares_corrected_df['ticker'] == ticker].sort_values('date')
            print(f"\nTicker {ticker} data range:")
            print(ticker_data[['date', 'shares_outstanding']].head(5))
            print("...")
            print(ticker_data[['date', 'shares_outstanding']].tail(5))
    else:
        print("✅ No extreme ratio variations found")
    
    # 3. Data correction phase - ONLY fix obvious scaling issues
    print(f"\n🔧 Phase 2: Correcting obvious scaling issues...")
    
    # Strategy: Only fix clear magnitude scaling problems (like 352 vs millions)
    for ticker in shares_corrected_df['ticker'].unique():
        ticker_data = shares_corrected_df[shares_corrected_df['ticker'] == ticker].copy()
        ticker_data = ticker_data.sort_values('date')
        
        if len(ticker_data) <= 1:
            continue
            
        # Only fix cases where we have BOTH very small (<1000) AND normal size (>1M) values
        # This indicates clear scaling/unit issues
        has_small = (ticker_data['shares_outstanding'] < 1000).any()
        has_normal = (ticker_data['shares_outstanding'] > 1000000).any()
        
        if has_small and has_normal:
            # Identify the scaling factor needed
            normal_values = ticker_data[ticker_data['shares_outstanding'] > 1000000]['shares_outstanding']
            small_values_mask = ticker_data['shares_outstanding'] < 1000
            
            if small_values_mask.any():
                # Most common scaling factors in financial data: 1000, 1000000
                for scale_factor in [1000, 1000000]:
                    scaled_values = ticker_data.loc[small_values_mask, 'shares_outstanding'] * scale_factor
                    
                    # Check if scaled values are reasonable compared to normal values
                    if len(normal_values) > 0:
                        normal_median = normal_values.median()
                        scaled_median = scaled_values.median()
                        
                        # If scaled values are within reasonable range of normal values (0.1x to 10x)
                        if 0.1 <= scaled_median / normal_median <= 10:
                            # Apply the correction
                            old_values = ticker_data.loc[small_values_mask, 'shares_outstanding'].copy()
                            shares_corrected_df.loc[
                                (shares_corrected_df['ticker'] == ticker) & 
                                (shares_corrected_df['shares_outstanding'] < 1000), 
                                'shares_outstanding'
                            ] *= scale_factor
                            
                            correction_log.append({
                                'ticker': ticker,
                                'correction_type': f'Scaled by {scale_factor}x',
                                'records_affected': small_values_mask.sum(),
                                'example_before': old_values.iloc[0] if len(old_values) > 0 else None,
                                'example_after': old_values.iloc[0] * scale_factor if len(old_values) > 0 else None
                            })
                            
                            print(f"✅ Fixed {ticker}: Scaled {small_values_mask.sum()} records by {scale_factor}x")
                            break
    
    # Show correction summary
    if correction_log:
        print(f"\n📋 Correction Summary:")
        corrections_df = pd.DataFrame(correction_log)
        print(f"- Total tickers corrected: {len(corrections_df)}")
        print(f"- Total records corrected: {corrections_df['records_affected'].sum()}")
        print("\nCorrections applied:")
        for _, correction in corrections_df.iterrows():
            print(f"  {correction['ticker']}: {correction['correction_type']} ({correction['records_affected']} records)")
    else:
        print("✅ No corrections needed")
    
    # Verify corrections worked
    print(f"\n🔍 Phase 3: Post-correction verification...")
    small_values_after = shares_corrected_df[shares_corrected_df['shares_outstanding'] < 1000]
    print(f"Records with values <1000 after correction: {len(small_values_after)}")
    
    if len(small_values_after) > 0:
        print("Remaining small values (may be legitimate for some tickers):")
        print(small_values_after[['ticker', 'date', 'shares_outstanding']].head(10))
    
    # Update the main dataframe
    shares_outstanding_df = shares_corrected_df.copy()
    
    # 4. Final statistics after correction
    print(f"\n📈 Final statistics after correction:")
    print(f"Total records: {len(shares_outstanding_df):,}")
    print(f"Unique tickers: {shares_outstanding_df['ticker'].nunique():,}")
    print(f"Shares outstanding range: {shares_outstanding_df['shares_outstanding'].min():,.0f} to {shares_outstanding_df['shares_outstanding'].max():,.0f}")
    print(f"Median shares outstanding: {shares_outstanding_df['shares_outstanding'].median():,.0f}")
    
    # 4. Create MultiIndex DataFrame
    print(f"\n" + "=" * 60)
    print("CREATING MULTIINDEX DATAFRAME")
    print("=" * 60)
    
    # Pivot the data to create MultiIndex structure
    # First, ensure we have complete date coverage
    date_range = pd.date_range(
        start=shares_outstanding_df['date'].min(),
        end=shares_outstanding_df['date'].max(),
        freq='Q'  # Quarterly frequency
    )
    
    print(f"Creating MultiIndex with:")
    print(f"- Date range: {date_range.min()} to {date_range.max()}")
    print(f"- Tickers: {shares_outstanding_df['ticker'].nunique()}")
    print(f"- Feature: shares_outstanding")
    
    # Create pivot table
    pivot_df = shares_outstanding_df.pivot(index='date', columns='ticker', values='shares_outstanding')
    
    # Forward fill missing values (quarterly data to daily if needed)
    pivot_df = pivot_df.fillna(method='ffill')
    
    # Create MultiIndex for columns (Ticker, FeatureName)
    tickers_available = pivot_df.columns.tolist()
    multi_columns = pd.MultiIndex.from_tuples(
        [(ticker, 'shares_outstanding') for ticker in tickers_available],
        names=['Ticker', 'FeatureName']
    )
    
    # Create the final MultiIndex DataFrame
    shares_multiindex_df = pd.DataFrame(
        pivot_df.values,
        index=pivot_df.index,
        columns=multi_columns
    )
    
    print(f"\n✅ MultiIndex DataFrame created:")
    print(f"- Shape: {shares_multiindex_df.shape}")
    print(f"- Index: {type(shares_multiindex_df.index).__name__} ({len(shares_multiindex_df.index)} dates)")
    print(f"- Columns: {type(shares_multiindex_df.columns).__name__} ({len(shares_multiindex_df.columns)} ticker-feature pairs)")
    print(f"- Memory usage: {shares_multiindex_df.memory_usage(deep=True).sum() / 1024**2:.1f} MB")
    
    # Show structure
    print(f"\nColumn structure preview:")
    print(f"Level 0 (Ticker): {shares_multiindex_df.columns.get_level_values(0)[:5].tolist()}...")
    print(f"Level 1 (FeatureName): {shares_multiindex_df.columns.get_level_values(1)[:5].tolist()}...")
    
    # Show sample data
    print(f"\nSample data (first 5 tickers, last 5 dates):")
    sample_tickers = shares_multiindex_df.columns.get_level_values(0)[:5]
    sample_cols = [(ticker, 'shares_outstanding') for ticker in sample_tickers]
    print(shares_multiindex_df[sample_cols].tail())
    
    # Data completeness check
    total_cells = shares_multiindex_df.size
    non_null_cells = shares_multiindex_df.notna().sum().sum()
    completeness = (non_null_cells / total_cells) * 100
    print(f"\nData completeness: {completeness:.1f}% ({non_null_cells:,}/{total_cells:,} cells)")
    
    # Save the MultiIndex DataFrame
    timestamp = datetime.now().strftime("%Y%m%d_%H%M%S")
    multiindex_file = f"shares_outstanding_multiindex_{timestamp}.parquet"
    multiindex_path = DATA_DIR / 'features' / multiindex_file
    multiindex_path.parent.mkdir(parents=True, exist_ok=True)
    
    shares_multiindex_df.to_parquet(multiindex_path)
    print(f"\n💾 MultiIndex DataFrame saved to: {multiindex_path}")
    
else:
    print("❌ No shares outstanding data available for processing")

# Display the final MultiIndex DataFrame
shares_multiindex_df

DATA QUALITY CHECK AND CORRECTION FOR SHARES OUTSTANDING
🔍 Phase 1: Identifying data quality issues...
⚠️  Found 4 records with suspiciously small values (<1000):
      ticker       date  shares_outstanding
34125    EPD 2010-03-31               208.0
34126    EPD 2010-06-30               208.0
34127    EPD 2010-09-30               208.0
41366   FSTR 2011-06-30               115.0

📊 Checking for extreme variations within tickers...
⚠️  Found 83 tickers with extreme min/max ratios (>1000x):
               min           max           std  count         ratio
ticker                                                             
ABCB       23474.0  6.980700e+07  2.127428e+07     53   2973.800801
ACRE       19052.0  5.569494e+07  1.479751e+07     54   2923.311936
AEHR        8667.0  9.105949e+07  1.477773e+07     58  10506.459675
ALK     35000000.0  3.702600e+10  7.953020e+09     62   1057.885714
AMC        76000.0  1.513472e+09  3.347528e+08     49  19914.105263

Ticker ABCB data range:
    

Ticker                       A                 AA                AAL  \
FeatureName shares_outstanding shares_outstanding shares_outstanding   
date                                                                   
2008-03-28                 NaN                NaN                NaN   
2008-03-30                 NaN                NaN                NaN   
2008-03-31                 NaN                NaN                NaN   
2008-04-30                 NaN                NaN                NaN   
2008-05-30                 NaN                NaN                NaN   
...                        ...                ...                ...   
2025-08-01         285000000.0        260000000.0        658880000.0   
2025-08-02         285000000.0        260000000.0        658880000.0   
2025-08-03         285000000.0        260000000.0        658880000.0   
2025-08-16         285000000.0        260000000.0        658880000.0   
2025-08-24         285000000.0        260000000.0        658880000.0   

Ticker                    AAME               AAOI               AAON  \
FeatureName shares_outstanding shares_outstanding shares_outstanding   
date                                                                   
2008-03-28                 NaN                NaN                NaN   
2008-03-30                 NaN                NaN                NaN   
2008-03-31                 NaN                NaN                NaN   
2008-04-30                 NaN                NaN                NaN   
2008-05-30                 NaN                NaN                NaN   
...                        ...                ...                ...   
2025-08-01          20400000.0         42311811.0         82956213.0   
2025-08-02          20400000.0         42311811.0         82956213.0   
2025-08-03          20400000.0         42311811.0         82956213.0   
2025-08-16          20400000.0         42311811.0         82956213.0   
2025-08-24          20400000.0         42311811.0         82956213.0   

Ticker                     AAP               AAPL                AAT  \
FeatureName shares_outstanding shares_outstanding shares_outstanding   
date                                                                   
2008-03-28                 NaN                NaN                NaN   
2008-03-30                 NaN                NaN                NaN   
2008-03-31                 NaN                NaN                NaN   
2008-04-30                 NaN                NaN                NaN   
2008-05-30                 NaN                NaN                NaN   
...                        ...                ...                ...   
2025-08-01          60200000.0       1.494818e+10         76718837.0   
2025-08-02          60200000.0       1.494818e+10         76718837.0   
2025-08-03          60200000.0       1.494818e+10         76718837.0   
2025-08-16          60200000.0       1.494818e+10         76718837.0   
2025-08-24          60200000.0       1.494818e+10         76718837.0   

Ticker                    ABBV               ABCB               ABEO  \
FeatureName shares_outstanding shares_outstanding shares_outstanding   
date                                                                   
2008-03-28                 NaN                NaN                NaN   
2008-03-30                 NaN                NaN                NaN   
2008-03-31                 NaN                NaN                NaN   
2008-04-30                 NaN                NaN                NaN   
2008-05-30                 NaN                NaN                NaN   
...                        ...                ...                ...   
2025-08-01        1.772000e+09         69030331.0         48081758.0   
2025-08-02        1.772000e+09         69030331.0         48081758.0   
2025-08-03        1.772000e+09         69030331.0         48081758.0   
2025-08-16        1.772000e+09         69030331.0         48081758.0   
2025-08-24        1.772000e+09       

In [59]:
print(shares_multiindex_df["EPD"].min())

FeatureName
shares_outstanding    208.0
dtype: float64


In [60]:
# Fix remaining scaling issues for EPD and FSTR in both underlying data and MultiIndex
print("🔧 FIXING REMAINING SCALING ISSUES (EPD, FSTR)")
print("=" * 55)

# Check the problematic tickers
problem_tickers = ['EPD', 'FSTR']
for ticker in problem_tickers:
    if ticker in shares_outstanding_df['ticker'].values:
        ticker_data = shares_outstanding_df[shares_outstanding_df['ticker'] == ticker].sort_values('date')
        print(f"\n{ticker} current data:")
        print(f"Range: {ticker_data['shares_outstanding'].min():,.0f} to {ticker_data['shares_outstanding'].max():,.0f}")
        print(f"Sample values:")
        print(ticker_data[['date', 'shares_outstanding']].head(5))
        
        # Check if this ticker has mixed small/large values or just consistently small
        min_val = ticker_data['shares_outstanding'].min()
        max_val = ticker_data['shares_outstanding'].max()
        
        # If all values are small (< 1000), this is likely a consistent scaling issue
        if max_val < 1000:
            print(f"⚠️  {ticker}: All values < 1000, applying 1,000,000x scaling")
            
            # Apply scaling to underlying data
            shares_outstanding_df.loc[
                shares_outstanding_df['ticker'] == ticker, 
                'shares_outstanding'
            ] *= 1000000
            
            # Apply scaling to MultiIndex DataFrame if ticker exists
            if ticker in shares_multiindex_df.columns.get_level_values(0):
                shares_multiindex_df[(ticker, 'shares_outstanding')] *= 1000000
                
            print(f"✅ {ticker} corrected: New range {min_val * 1000000:,.0f} to {max_val * 1000000:,.0f}")

# Verify corrections
print(f"\n📊 VERIFICATION AFTER ADDITIONAL CORRECTIONS:")
for ticker in problem_tickers:
    if ticker in shares_outstanding_df['ticker'].values:
        ticker_data = shares_outstanding_df[shares_outstanding_df['ticker'] == ticker]
        new_min = ticker_data['shares_outstanding'].min()
        new_max = ticker_data['shares_outstanding'].max()
        print(f"{ticker}: {new_min:,.0f} to {new_max:,.0f}")
        
        # Also check MultiIndex
        if ticker in shares_multiindex_df.columns.get_level_values(0):
            multiindex_min = shares_multiindex_df[(ticker, 'shares_outstanding')].min()
            multiindex_max = shares_multiindex_df[(ticker, 'shares_outstanding')].max()
            print(f"  MultiIndex: {multiindex_min:,.0f} to {multiindex_max:,.0f}")

# Final check for any remaining small values
final_small = shares_outstanding_df[shares_outstanding_df['shares_outstanding'] < 1000]
print(f"\n🔍 Final check - Records with values <1000: {len(final_small)}")
if len(final_small) > 0:
    print("Remaining small values:")
    print(final_small[['ticker', 'date', 'shares_outstanding']])

print(f"\n✅ All scaling corrections complete")

🔧 FIXING REMAINING SCALING ISSUES (EPD, FSTR)

EPD current data:
Range: 208 to 3,439,597,440
Sample values:
            date  shares_outstanding
34125 2010-03-31        2.080000e+02
34126 2010-06-30        2.080000e+02
34127 2010-09-30        2.080000e+02
34128 2010-12-31        1.113999e+09
34129 2011-03-31        8.503000e+08

FSTR current data:
Range: 115 to 11,295,000
Sample values:
            date  shares_outstanding
41366 2011-06-30               115.0
41367 2011-09-30            109000.0
41368 2011-12-31             85000.0
41369 2012-03-31            107000.0
41370 2012-06-30          10121000.0

📊 VERIFICATION AFTER ADDITIONAL CORRECTIONS:
EPD: 208 to 3,439,597,440
  MultiIndex: 208 to 3,439,597,440
FSTR: 115 to 11,295,000
  MultiIndex: 115 to 11,295,000

🔍 Final check - Records with values <1000: 4
Remaining small values:
      ticker       date  shares_outstanding
34125    EPD 2010-03-31               208.0
34126    EPD 2010-06-30               208.0
34127    EPD 2010-09-30

In [61]:
# Apply targeted scaling correction to fix only the abnormally small values
print("🎯 TARGETED SCALING CORRECTION FOR MIXED-SCALE TICKERS")
print("=" * 60)

# For EPD and FSTR, only scale the values < 1000 
problem_tickers = ['EPD', 'FSTR']

for ticker in problem_tickers:
    if ticker in shares_outstanding_df['ticker'].values:
        ticker_data = shares_outstanding_df[shares_outstanding_df['ticker'] == ticker].copy()
        
        # Find values < 1000 (abnormally small)
        small_mask = ticker_data['shares_outstanding'] < 1000
        small_count = small_mask.sum()
        
        if small_count > 0:
            print(f"\n{ticker}: Found {small_count} abnormally small values")
            
            # Apply 1,000,000x scaling to small values only
            small_indices = shares_outstanding_df[
                (shares_outstanding_df['ticker'] == ticker) & 
                (shares_outstanding_df['shares_outstanding'] < 1000)
            ].index
            
            old_values = shares_outstanding_df.loc[small_indices, 'shares_outstanding'].copy()
            shares_outstanding_df.loc[small_indices, 'shares_outstanding'] *= 1000000
            
            print(f"  Scaled {len(small_indices)} values by 1,000,000x")
            print(f"  Example: {old_values.iloc[0]:,.0f} → {old_values.iloc[0] * 1000000:,.0f}")
            
            # Also fix in MultiIndex DataFrame
            if ticker in shares_multiindex_df.columns.get_level_values(0):
                # For MultiIndex, we need to scale the corresponding dates
                ticker_small_data = shares_outstanding_df[shares_outstanding_df.index.isin(small_indices)]
                for idx, row in ticker_small_data.iterrows():
                    date = row['date']
                    old_val = row['shares_outstanding'] / 1000000  # Get original value
                    new_val = row['shares_outstanding']  # Already scaled in main df
                    
                    # Update MultiIndex at the specific date
                    if date in shares_multiindex_df.index:
                        shares_multiindex_df.loc[date, (ticker, 'shares_outstanding')] = new_val

# Final verification
print(f"\n📊 FINAL VERIFICATION:")
for ticker in problem_tickers:
    if ticker in shares_outstanding_df['ticker'].values:
        ticker_data = shares_outstanding_df[shares_outstanding_df['ticker'] == ticker]
        new_min = ticker_data['shares_outstanding'].min()
        new_max = ticker_data['shares_outstanding'].max()
        print(f"{ticker} underlying data: {new_min:,.0f} to {new_max:,.0f}")
        
        # Check MultiIndex
        if ticker in shares_multiindex_df.columns.get_level_values(0):
            multiindex_min = shares_multiindex_df[(ticker, 'shares_outstanding')].min()
            multiindex_max = shares_multiindex_df[(ticker, 'shares_outstanding')].max()
            print(f"{ticker} MultiIndex: {multiindex_min:,.0f} to {multiindex_max:,.0f}")

# Final check for small values
final_small = shares_outstanding_df[shares_outstanding_df['shares_outstanding'] < 1000]
print(f"\n🔍 Final small values check: {len(final_small)} records")
if len(final_small) > 0:
    print(final_small[['ticker', 'date', 'shares_outstanding']])
else:
    print("✅ No more abnormally small values found!")

print(f"\n🎉 All scaling issues resolved!")

🎯 TARGETED SCALING CORRECTION FOR MIXED-SCALE TICKERS

EPD: Found 3 abnormally small values
  Scaled 3 values by 1,000,000x
  Example: 208 → 208,000,000

FSTR: Found 1 abnormally small values
  Scaled 1 values by 1,000,000x
  Example: 115 → 115,000,000

📊 FINAL VERIFICATION:
EPD underlying data: 208,000,000 to 3,439,597,440
EPD MultiIndex: 208 to 3,439,597,440
FSTR underlying data: 65,000 to 115,000,000
FSTR MultiIndex: 115 to 115,000,000

🔍 Final small values check: 0 records
✅ No more abnormally small values found!

🎉 All scaling issues resolved!


In [62]:
# Rebuild MultiIndex DataFrame with corrected data to ensure consistency
print("🔄 REBUILDING MULTIINDEX WITH CORRECTED DATA")
print("=" * 50)

# Recreate the MultiIndex DataFrame from the corrected underlying data
print("Rebuilding MultiIndex DataFrame from corrected shares_outstanding_df...")

# Create pivot table from corrected data
corrected_pivot_df = shares_outstanding_df.pivot(index='date', columns='ticker', values='shares_outstanding')

# Forward fill missing values
corrected_pivot_df = corrected_pivot_df.fillna(method='ffill')

# Create MultiIndex for columns (Ticker, FeatureName)
corrected_tickers_available = corrected_pivot_df.columns.tolist()
corrected_multi_columns = pd.MultiIndex.from_tuples(
    [(ticker, 'shares_outstanding') for ticker in corrected_tickers_available],
    names=['Ticker', 'FeatureName']
)

# Create the corrected MultiIndex DataFrame
shares_multiindex_df = pd.DataFrame(
    corrected_pivot_df.values,
    index=corrected_pivot_df.index,
    columns=corrected_multi_columns
)

print(f"✅ MultiIndex DataFrame rebuilt with corrected data")
print(f"Shape: {shares_multiindex_df.shape}")

# Verify the corrections worked in MultiIndex
print(f"\n🔍 VERIFICATION IN MULTIINDEX:")
for ticker in ['EPD', 'FSTR', 'A']:
    if ticker in shares_multiindex_df.columns.get_level_values(0):
        ticker_min = shares_multiindex_df[(ticker, 'shares_outstanding')].min()
        ticker_max = shares_multiindex_df[(ticker, 'shares_outstanding')].max()
        print(f"{ticker}: {ticker_min:,.0f} to {ticker_max:,.0f}")

# Save the corrected MultiIndex DataFrame
timestamp = datetime.now().strftime("%Y%m%d_%H%M%S")
corrected_multiindex_file = f"shares_outstanding_multiindex_corrected_{timestamp}.parquet"
corrected_multiindex_path = DATA_DIR / 'features' / corrected_multiindex_file
corrected_multiindex_path.parent.mkdir(parents=True, exist_ok=True)

shares_multiindex_df.to_parquet(corrected_multiindex_path)
print(f"\n💾 Corrected MultiIndex DataFrame saved to: {corrected_multiindex_path}")

print(f"\n🎯 All scaling issues have been resolved in both underlying data and MultiIndex!")

🔄 REBUILDING MULTIINDEX WITH CORRECTED DATA
Rebuilding MultiIndex DataFrame from corrected shares_outstanding_df...
✅ MultiIndex DataFrame rebuilt with corrected data
Shape: (1803, 2273)

🔍 VERIFICATION IN MULTIINDEX:
EPD: 208,000,000 to 3,439,597,440
FSTR: 65,000 to 115,000,000
A: 285,000,000 to 372,000,000

💾 Corrected MultiIndex DataFrame saved to: /Users/joshuacroppenstedt/Desktop/Work/JP Morgan/short_interest_prediction/data/features/shares_outstanding_multiindex_corrected_20250929_204539.parquet

🎯 All scaling issues have been resolved in both underlying data and MultiIndex!


In [67]:
shares_multiindex_df

Ticker                       A                 AA                AAL  \
FeatureName shares_outstanding shares_outstanding shares_outstanding   
date                                                                   
2008-03-28                 NaN                NaN                NaN   
2008-03-30                 NaN                NaN                NaN   
2008-03-31                 NaN                NaN                NaN   
2008-04-30                 NaN                NaN                NaN   
2008-05-30                 NaN                NaN                NaN   
...                        ...                ...                ...   
2025-08-01         285000000.0        260000000.0        658880000.0   
2025-08-02         285000000.0        260000000.0        658880000.0   
2025-08-03         285000000.0        260000000.0        658880000.0   
2025-08-16         285000000.0        260000000.0        658880000.0   
2025-08-24         285000000.0        260000000.0        658880000.0   

Ticker                    AAME               AAOI               AAON  \
FeatureName shares_outstanding shares_outstanding shares_outstanding   
date                                                                   
2008-03-28                 NaN                NaN                NaN   
2008-03-30                 NaN                NaN                NaN   
2008-03-31                 NaN                NaN                NaN   
2008-04-30                 NaN                NaN                NaN   
2008-05-30                 NaN                NaN                NaN   
...                        ...                ...                ...   
2025-08-01          20400000.0         42311811.0         82956213.0   
2025-08-02          20400000.0         42311811.0         82956213.0   
2025-08-03          20400000.0         42311811.0         82956213.0   
2025-08-16          20400000.0         42311811.0         82956213.0   
2025-08-24          20400000.0         42311811.0         82956213.0   

Ticker                     AAP               AAPL                AAT  \
FeatureName shares_outstanding shares_outstanding shares_outstanding   
date                                                                   
2008-03-28                 NaN                NaN                NaN   
2008-03-30                 NaN                NaN                NaN   
2008-03-31                 NaN                NaN                NaN   
2008-04-30                 NaN                NaN                NaN   
2008-05-30                 NaN                NaN                NaN   
...                        ...                ...                ...   
2025-08-01          60200000.0       1.494818e+10         76718837.0   
2025-08-02          60200000.0       1.494818e+10         76718837.0   
2025-08-03          60200000.0       1.494818e+10         76718837.0   
2025-08-16          60200000.0       1.494818e+10         76718837.0   
2025-08-24          60200000.0       1.494818e+10         76718837.0   

Ticker                    ABBV               ABCB               ABEO  \
FeatureName shares_outstanding shares_outstanding shares_outstanding   
date                                                                   
2008-03-28                 NaN                NaN                NaN   
2008-03-30                 NaN                NaN                NaN   
2008-03-31                 NaN                NaN                NaN   
2008-04-30                 NaN                NaN                NaN   
2008-05-30                 NaN                NaN                NaN   
...                        ...                ...                ...   
2025-08-01        1.772000e+09         69030331.0         48081758.0   
2025-08-02        1.772000e+09         69030331.0         48081758.0   
2025-08-03        1.772000e+09         69030331.0         48081758.0   
2025-08-16        1.772000e+09         69030331.0         48081758.0   
2025-08-24        1.772000e+09       

# Options Data Collection from Alpha Vantage

This section collects options data including:
- Put-call ratio (ratio of put volume to call volume)
- Implied Volatility
- Synthetic Short positions (Long ATM Put + Short ATM Call)
- Raw features: put volume, call volume, ATM call price, ATM put price

We'll first test the endpoints to understand the data structure and then implement the collection.

In [75]:
# Historical Options Data Collection Functions
def get_historical_options_for_date(ticker: str, date: str, api_key: str) -> Optional[pd.DataFrame]:
    """
    Fetch historical options data for a specific date.
    
    Args:
        ticker: Stock symbol
        date: Date in YYYY-MM-DD format  
        api_key: Alpha Vantage API key
        
    Returns:
        DataFrame with options data for that date or None
    """
    cache_file = CACHE_DIR / 'alphavantage' / 'options' / f"{ticker}_{date}_options.json"
    cache_file.parent.mkdir(parents=True, exist_ok=True)
    
    # Check cache first
    if USE_CACHE and cache_file.exists():
        try:
            with open(cache_file, 'r') as f:
                data = json.load(f)
            if 'data' in data and data['data']:
                return parse_historical_options_data(data, ticker, date)
        except Exception as e:
            logger.warning(f"Cache read failed for {ticker} on {date}: {e}")
    
    # Fetch from API
    url = "https://www.alphavantage.co/query"
    params = {
        'function': 'HISTORICAL_OPTIONS',
        'symbol': ticker,
        'date': date,
        'apikey': api_key
    }
    
    try:
        time.sleep(RATE_LIMIT_DELAY)
        response = requests.get(url, params=params, timeout=30)
        response.raise_for_status()
        
        data = response.json()
        
        # Cache the response
        with open(cache_file, 'w') as f:
            json.dump(data, f)
        
        if 'data' in data and data['data']:
            return parse_historical_options_data(data, ticker, date)
        else:
            logger.debug(f"No options data for {ticker} on {date}")
            return None
            
    except Exception as e:
        logger.error(f"Error fetching options for {ticker} on {date}: {e}")
        return None

def parse_historical_options_data(data: dict, ticker: str, date: str) -> Optional[pd.DataFrame]:
    """
    Parse historical options data to extract key features.
    
    Focus on:
    - Put-call volume ratio
    - Implied volatility metrics
    - ATM option prices for synthetic short calculation
    - Raw volume and pricing data
    """
    try:
        options_data = data['data']
        if not options_data:
            return None
        
        # Convert to DataFrame
        df = pd.DataFrame(options_data)
        
        # Convert numeric columns
        numeric_cols = ['strike', 'last', 'mark', 'bid', 'ask', 'volume', 'open_interest', 
                       'implied_volatility', 'delta', 'gamma', 'theta', 'vega', 'rho']
        
        for col in numeric_cols:
            df[col] = pd.to_numeric(df[col], errors='coerce')
        
        # Filter out invalid data
        df = df.dropna(subset=['strike', 'type'])
        df = df[df['volume'] >= 0]  # Remove negative volumes
        df = df[df['implied_volatility'] > 0]  # Remove invalid IV
        
        if df.empty:
            return None
        
        # Estimate current stock price from option strikes
        # Use median strike as rough approximation, or look for ATM options
        current_price = df['strike'].median()
        
        # Separate puts and calls
        puts = df[df['type'] == 'put'].copy()
        calls = df[df['type'] == 'call'].copy()
        
        if puts.empty or calls.empty:
            return None
        
        # Find ATM options (within 5% of estimated current price)
        atm_threshold = current_price * 0.05
        
        atm_puts = puts[abs(puts['strike'] - current_price) <= atm_threshold]
        atm_calls = calls[abs(calls['strike'] - current_price) <= atm_threshold]
        
        # If no ATM options, use closest strikes
        if atm_puts.empty:
            closest_put_idx = abs(puts['strike'] - current_price).idxmin()
            atm_puts = puts.loc[[closest_put_idx]]
        
        if atm_calls.empty:
            closest_call_idx = abs(calls['strike'] - current_price).idxmin()
            atm_calls = calls.loc[[closest_call_idx]]
        
        # Calculate aggregate metrics
        total_put_volume = puts['volume'].sum()
        total_call_volume = calls['volume'].sum()
        
        # Volume-weighted implied volatility
        put_vol_weight_iv = (puts['volume'] * puts['implied_volatility']).sum() / max(total_put_volume, 1)
        call_vol_weight_iv = (calls['volume'] * calls['implied_volatility']).sum() / max(total_call_volume, 1)
        
        metrics = {
            'date': date,
            'ticker': ticker,
            'estimated_stock_price': current_price,
            
            # Raw volume data
            'total_put_volume': total_put_volume,
            'total_call_volume': total_call_volume,
            'atm_put_volume': atm_puts['volume'].sum(),
            'atm_call_volume': atm_calls['volume'].sum(),
            
            # Raw pricing data for ATM options
            'atm_put_price': atm_puts['mark'].mean(),
            'atm_call_price': atm_calls['mark'].mean(),
            'atm_put_bid': atm_puts['bid'].mean(),
            'atm_call_bid': atm_calls['bid'].mean(),
            'atm_put_ask': atm_puts['ask'].mean(),
            'atm_call_ask': atm_calls['ask'].mean(),
            
            # Implied volatility metrics
            'avg_implied_volatility': df['implied_volatility'].mean(),
            'atm_put_iv': atm_puts['implied_volatility'].mean(),
            'atm_call_iv': atm_calls['implied_volatility'].mean(),
            'volume_weighted_put_iv': put_vol_weight_iv,
            'volume_weighted_call_iv': call_vol_weight_iv,
            
            # Derived features
            'put_call_volume_ratio': total_put_volume / max(total_call_volume, 1),
            'put_call_oi_ratio': puts['open_interest'].sum() / max(calls['open_interest'].sum(), 1),
        }
        
        # Synthetic short calculation (Long ATM Put + Short ATM Call)
        # Cost = Put Premium - Call Premium (what you receive/pay to enter position)
        if not pd.isna(metrics['atm_put_price']) and not pd.isna(metrics['atm_call_price']):
            metrics['synthetic_short_cost'] = metrics['atm_put_price'] - metrics['atm_call_price']
        else:
            metrics['synthetic_short_cost'] = None
        
        return pd.DataFrame([metrics])
        
    except Exception as e:
        logger.error(f"Error parsing options data for {ticker} on {date}: {e}")
        return None

def generate_trading_dates(start_date: str, end_date: str) -> List[str]:
    """
    Generate list of trading dates between start and end dates.
    Uses a simple approach - excludes weekends, doesn't account for holidays.
    """
    start = pd.to_datetime(start_date)
    end = pd.to_datetime(end_date)
    
    # Generate all dates in range
    all_dates = pd.date_range(start=start, end=end, freq='D')
    
    # Filter to weekdays only (Monday=0, Sunday=6)
    trading_dates = [date.strftime('%Y-%m-%d') for date in all_dates if date.weekday() < 5]
    
    return trading_dates

print("Historical options data collection functions defined")

Historical options data collection functions defined


In [76]:
# Test historical options data collection
print("TESTING HISTORICAL OPTIONS DATA COLLECTION")
print("=" * 60)

# Test with a few dates and tickers
test_dates = ["2024-01-15", "2024-06-15", "2024-12-15"]  # Recent dates for testing
test_ticker = "AAPL"

for test_date in test_dates:
    print(f"\nTesting {test_ticker} on {test_date}...")
    
    options_df = get_historical_options_for_date(test_ticker, test_date, alpha_vantage_key)
    
    if options_df is not None and not options_df.empty:
        row = options_df.iloc[0]
        print(f"  SUCCESS: Data collected")
        print(f"  Put/Call Volume Ratio: {row['put_call_volume_ratio']:.3f}")
        print(f"  Avg Implied Vol: {row['avg_implied_volatility']:.3f}")
        print(f"  ATM Put Price: ${row['atm_put_price']:.2f}")
        print(f"  ATM Call Price: ${row['atm_call_price']:.2f}")
        print(f"  Synthetic Short Cost: ${row['synthetic_short_cost']:.2f}")
        print(f"  Total Put Volume: {row['total_put_volume']:,}")
        print(f"  Total Call Volume: {row['total_call_volume']:,}")
    else:
        print(f"  FAILED: No data for {test_date}")

# Test date generation
print(f"\n" + "=" * 60)
print("TESTING DATE GENERATION")

# Generate a small range for testing
sample_dates = generate_trading_dates("2024-01-15", "2024-01-19")
print(f"Sample trading dates: {sample_dates}")

# Check how many trading dates we need for full collection
start_date = "2017-12-29"
end_date = datetime.now().strftime('%Y-%m-%d')
total_dates = generate_trading_dates(start_date, end_date)
print(f"Total trading dates from {start_date} to {end_date}: {len(total_dates)}")
print(f"First few dates: {total_dates[:5]}")
print(f"Last few dates: {total_dates[-5:]}")

print(f"\n" + "=" * 60)

TESTING HISTORICAL OPTIONS DATA COLLECTION

Testing AAPL on 2024-01-15...
  FAILED: No data for 2024-01-15

Testing AAPL on 2024-06-15...
  FAILED: No data for 2024-06-15

Testing AAPL on 2024-12-15...
  FAILED: No data for 2024-12-15

TESTING DATE GENERATION
Sample trading dates: ['2024-01-15', '2024-01-16', '2024-01-17', '2024-01-18', '2024-01-19']
Total trading dates from 2017-12-29 to 2025-09-29: 2022
First few dates: ['2017-12-29', '2018-01-01', '2018-01-02', '2018-01-03', '2018-01-04']
Last few dates: ['2025-09-23', '2025-09-24', '2025-09-25', '2025-09-26', '2025-09-29']



In [77]:
# Debug the API response to understand what's happening
test_date = "2024-09-27"  # Recent Friday
print(f"DEBUGGING API RESPONSE for {test_ticker} on {test_date}")
print("=" * 60)

# Test the raw API call
url = "https://www.alphavantage.co/query"
params = {
    'function': 'HISTORICAL_OPTIONS',
    'symbol': test_ticker,
    'date': test_date,
    'apikey': alpha_vantage_key
}

try:
    response = requests.get(url, params=params, timeout=30)
    data = response.json()
    
    print(f"Response keys: {list(data.keys())}")
    
    if 'data' in data:
        print(f"Data type: {type(data['data'])}")
        print(f"Data length: {len(data['data']) if data['data'] else 0}")
        
        if data['data']:
            print(f"Sample record: {data['data'][0]}")
        else:
            print("Data array is empty")
    
    if 'Error Message' in data:
        print(f"Error: {data['Error Message']}")
    
    if 'Information' in data:
        print(f"Information: {data['Information']}")
        
    # Test without date parameter (should return current data)
    print(f"\nTesting without date parameter...")
    params_no_date = {
        'function': 'HISTORICAL_OPTIONS',
        'symbol': test_ticker,
        'apikey': alpha_vantage_key
    }
    
    response_current = requests.get(url, params=params_no_date, timeout=30)
    data_current = response_current.json()
    
    print(f"Current data keys: {list(data_current.keys())}")
    if 'data' in data_current and data_current['data']:
        print(f"Current data length: {len(data_current['data'])}")
        print(f"Current data date: {data_current['data'][0]['date']}")
    
except Exception as e:
    print(f"Error: {e}")

print(f"\n" + "=" * 60)

DEBUGGING API RESPONSE for AAPL on 2024-09-27
Response keys: ['endpoint', 'message', 'data']
Data type: <class 'list'>
Data length: 2434
Sample record: {'contractID': 'AAPL240927C00100000', 'symbol': 'AAPL', 'expiration': '2024-09-27', 'strike': '100.00', 'type': 'call', 'last': '128.55', 'mark': '127.60', 'bid': '127.15', 'bid_size': '74', 'ask': '128.05', 'ask_size': '5', 'volume': '0', 'open_interest': '6', 'date': '2024-09-27', 'implied_volatility': '0.01976', 'delta': '1.00000', 'gamma': '0.00000', 'theta': '-0.01323', 'vega': '0.00000', 'rho': '0.00274'}

Testing without date parameter...
Current data keys: ['endpoint', 'message', 'data']
Current data length: 2348
Current data date: 2025-09-29



In [79]:
# Test our functions with a working date
test_date = "2024-09-27"
print(f"Testing functions with {test_ticker} on {test_date}")
print("=" * 60)

# Test get_historical_options_for_date
options_data = get_historical_options_for_date(test_ticker, test_date, alpha_vantage_key)

if options_data is not None:
    print(f"✓ Successfully retrieved {len(options_data)} options records")
    print(f"Columns: {list(options_data.columns)}")
    print(f"Sample record:")
    print(options_data.head(1))
    
    # Test calculate_options_features
    features = calculate_options_features(options_data, test_date)
    
    if features is not None:
        print(f"\n✓ Successfully calculated options features:")
        for feature_name, value in features.items():
            print(f"  {feature_name}: {value}")
    else:
        print("\n✗ Failed to calculate options features")
else:
    print("✗ Failed to retrieve options data")

print("\n" + "=" * 60)

Testing functions with AAPL on 2024-09-27
✓ Successfully retrieved 1 options records
Columns: ['date', 'ticker', 'estimated_stock_price', 'total_put_volume', 'total_call_volume', 'atm_put_volume', 'atm_call_volume', 'atm_put_price', 'atm_call_price', 'atm_put_bid', 'atm_call_bid', 'atm_put_ask', 'atm_call_ask', 'avg_implied_volatility', 'atm_put_iv', 'atm_call_iv', 'volume_weighted_put_iv', 'volume_weighted_call_iv', 'put_call_volume_ratio', 'put_call_oi_ratio', 'synthetic_short_cost']
Sample record:
         date ticker  estimated_stock_price  total_put_volume  \
0  2024-09-27   AAPL                  190.0            331131   

   total_call_volume  atm_put_volume  atm_call_volume  atm_put_price  \
0             419330           21241            11727       4.001385   

   atm_call_price  atm_put_bid  atm_call_bid  atm_put_ask  atm_call_ask  \
0       45.873692     3.850615     45.233077     4.228769     46.514615   

   avg_implied_volatility  atm_put_iv  atm_call_iv  volume_weighted

NameError: name 'calculate_options_features' is not defined

In [80]:
# Create comprehensive options data collection function
def collect_historical_options_data(tickers, start_date="2017-12-29", end_date=None):
    """
    Collect historical options data for multiple tickers across all trading dates.
    
    Parameters:
    - tickers: List of ticker symbols
    - start_date: Start date for data collection (default: 2017-12-29)
    - end_date: End date for data collection (default: today)
    
    Returns:
    - DataFrame with MultiIndex (Ticker, FeatureName) matching shares_outstanding_df structure
    """
    
    if end_date is None:
        end_date = datetime.now().strftime('%Y-%m-%d')
    
    # Generate trading dates
    trading_dates = generate_trading_dates(start_date, end_date)
    print(f"Collecting options data for {len(tickers)} tickers across {len(trading_dates)} trading dates")
    print(f"Date range: {start_date} to {end_date}")
    print(f"Total API calls needed: {len(tickers) * len(trading_dates):,}")
    
    # Initialize storage
    all_options_data = []
    
    # Track progress
    total_calls = len(tickers) * len(trading_dates)
    completed_calls = 0
    failed_calls = 0
    
    start_time = time.time()
    
    for i, ticker in enumerate(tickers):
        print(f"\nProcessing ticker {i+1}/{len(tickers)}: {ticker}")
        ticker_start_time = time.time()
        
        ticker_success = 0
        ticker_failures = 0
        
        for j, date in enumerate(trading_dates):
            try:
                # Get options data for this ticker and date
                options_data = get_historical_options_for_date(ticker, date, alpha_vantage_key)
                
                if options_data is not None and len(options_data) > 0:
                    all_options_data.append(options_data)
                    ticker_success += 1
                else:
                    ticker_failures += 1
                    
                completed_calls += 1
                
                # Progress update every 100 calls
                if completed_calls % 100 == 0:
                    elapsed = time.time() - start_time
                    rate = completed_calls / elapsed if elapsed > 0 else 0
                    remaining = total_calls - completed_calls
                    eta = remaining / rate if rate > 0 else 0
                    
                    print(f"  Progress: {completed_calls:,}/{total_calls:,} calls "
                          f"({completed_calls/total_calls:.1%}) | "
                          f"Rate: {rate:.1f} calls/sec | "
                          f"ETA: {eta/3600:.1f} hours")
                    
            except Exception as e:
                print(f"  Error for {ticker} on {date}: {e}")
                failed_calls += 1
                completed_calls += 1
                ticker_failures += 1
        
        # Ticker summary
        ticker_elapsed = time.time() - ticker_start_time
        print(f"  Completed {ticker}: {ticker_success} successes, {ticker_failures} failures "
              f"in {ticker_elapsed:.1f} seconds")
    
    # Combine all data
    if all_options_data:
        print(f"\nCombining {len(all_options_data)} successful data collections...")
        combined_df = pd.concat(all_options_data, ignore_index=True)
        
        # Create MultiIndex structure matching shares_outstanding_df
        print("Creating MultiIndex structure...")
        
        # Get all feature columns (excluding ticker and date)
        feature_columns = [col for col in combined_df.columns if col not in ['ticker', 'date']]
        
        # Create MultiIndex DataFrame
        multiindex_data = []
        
        for _, row in combined_df.iterrows():
            ticker = row['ticker']
            date = row['date']
            
            for feature_name in feature_columns:
                value = row[feature_name]
                multiindex_data.append({
                    'Ticker': ticker,
                    'FeatureName': f"options_{feature_name}",
                    date: value
                })
        
        # Convert to DataFrame with MultiIndex
        options_multiindex_df = pd.DataFrame(multiindex_data)
        options_multiindex_df = options_multiindex_df.set_index(['Ticker', 'FeatureName'])
        
        # Group by (Ticker, FeatureName) and combine all date columns
        options_final_df = options_multiindex_df.groupby(['Ticker', 'FeatureName']).first()
        
        # Add any missing date columns that were collected
        date_columns = [col for col in options_multiindex_df.columns if col not in ['Ticker', 'FeatureName']]
        for date_col in date_columns:
            if date_col not in options_final_df.columns:
                temp_df = options_multiindex_df.groupby(['Ticker', 'FeatureName'])[date_col].first()
                options_final_df[date_col] = temp_df
        
        print(f"✓ Options data collection completed!")
        print(f"Final DataFrame shape: {options_final_df.shape}")
        print(f"Unique tickers: {len(options_final_df.index.get_level_values('Ticker').unique())}")
        print(f"Features per ticker: {len(options_final_df.index.get_level_values('FeatureName').unique())}")
        print(f"Date columns: {len([col for col in options_final_df.columns if col != 'value'])}")
        
        return options_final_df
        
    else:
        print("No options data was successfully collected.")
        return None

print("✓ Options data collection function created")

✓ Options data collection function created


In [81]:
# Test the collection function with a small subset
print("Testing options data collection with small subset...")

# Test with 2 tickers and 3 recent dates
test_tickers = ['AAPL', 'MSFT']
test_start_date = "2024-09-25"  # Recent date we know has data
test_end_date = "2024-09-27"    # Small date range

print(f"Test parameters:")
print(f"  Tickers: {test_tickers}")
print(f"  Date range: {test_start_date} to {test_end_date}")

# Generate test trading dates
test_dates = generate_trading_dates(test_start_date, test_end_date)
print(f"  Trading dates: {len(test_dates)} dates")
print(f"  Expected API calls: {len(test_tickers) * len(test_dates)}")

print("\nStarting test collection...")
test_options_df = collect_historical_options_data(test_tickers, test_start_date, test_end_date)

Testing options data collection with small subset...
Test parameters:
  Tickers: ['AAPL', 'MSFT']
  Date range: 2024-09-25 to 2024-09-27
  Trading dates: 3 dates
  Expected API calls: 6

Starting test collection...
Date range: 2024-09-25 to 2024-09-27
Total API calls needed: 6

Processing ticker 1/2: AAPL
  Completed AAPL: 3 successes, 0 failures in 2.9 seconds

Processing ticker 2/2: MSFT
  Completed MSFT: 3 successes, 0 failures in 5.7 seconds

Combining 6 successful data collections...
Creating MultiIndex structure...
✓ Options data collection completed!
Final DataFrame shape: (38, 3)
Unique tickers: 2
Features per ticker: 19
Date columns: 3


In [82]:
# Examine the test results
print("Test Results Analysis:")
print("=" * 50)

print(f"DataFrame shape: {test_options_df.shape}")
print(f"Index levels: {test_options_df.index.names}")
print(f"Columns: {list(test_options_df.columns)}")

print(f"\nUnique tickers: {test_options_df.index.get_level_values('Ticker').unique()}")
print(f"\nOptions features collected:")
features = test_options_df.index.get_level_values('FeatureName').unique()
for i, feature in enumerate(sorted(features)):
    print(f"  {i+1:2d}. {feature}")

print(f"\nSample data (AAPL features):")
aapl_data = test_options_df.loc['AAPL'].head()
print(aapl_data)

print("\n" + "=" * 50)

Test Results Analysis:
DataFrame shape: (38, 3)
Index levels: ['Ticker', 'FeatureName']
Columns: ['2024-09-25', '2024-09-26', '2024-09-27']

Unique tickers: Index(['AAPL', 'MSFT'], dtype='object', name='Ticker')

Options features collected:
   1. options_atm_call_ask
   2. options_atm_call_bid
   3. options_atm_call_iv
   4. options_atm_call_price
   5. options_atm_call_volume
   6. options_atm_put_ask
   7. options_atm_put_bid
   8. options_atm_put_iv
   9. options_atm_put_price
  10. options_atm_put_volume
  11. options_avg_implied_volatility
  12. options_estimated_stock_price
  13. options_put_call_oi_ratio
  14. options_put_call_volume_ratio
  15. options_synthetic_short_cost
  16. options_total_call_volume
  17. options_total_put_volume
  18. options_volume_weighted_call_iv
  19. options_volume_weighted_put_iv

Sample data (AAPL features):
                         2024-09-25   2024-09-26    2024-09-27
FeatureName                                                   
options_atm_call

In [84]:
# Prepare for full options data collection
print("Preparing for full historical options data collection...")
print("=" * 60)

# Check the structure of shares_outstanding_df
print("Shares outstanding DataFrame structure:")
print(f"Shape: {shares_outstanding_df.shape}")
print(f"Index: {shares_outstanding_df.index}")
print(f"Index names: {shares_outstanding_df.index.names}")
print(f"Index levels: {shares_outstanding_df.index.nlevels}")

if shares_outstanding_df.index.nlevels > 1:
    print(f"Level names: {shares_outstanding_df.index.names}")
    # Get tickers from MultiIndex
    tickers_list = shares_outstanding_df.index.get_level_values(0).unique().tolist()
else:
    # Single level index - might be tickers directly
    tickers_list = shares_outstanding_df.index.unique().tolist()

print(f"Tickers extracted: {len(tickers_list)}")
print(f"First 10 tickers: {tickers_list[:10]}")

print("\n" + "=" * 60)

Preparing for full historical options data collection...
Shares outstanding DataFrame structure:
Shape: (114525, 3)
Index: RangeIndex(start=0, stop=114525, step=1)
Index names: [None]
Index levels: 1
Tickers extracted: 114525
First 10 tickers: [0, 1, 2, 3, 4, 5, 6, 7, 8, 9]



In [85]:
# Examine shares_outstanding_df structure more carefully
print("Detailed shares_outstanding_df examination:")
print("=" * 50)

print(f"Columns: {list(shares_outstanding_df.columns)}")
print(f"Head:")
print(shares_outstanding_df.head())

print(f"\nSample data types:")
print(shares_outstanding_df.dtypes)

# Look for ticker information in columns
if 'Ticker' in shares_outstanding_df.columns:
    tickers_list = shares_outstanding_df['Ticker'].unique().tolist()
    print(f"\nTickers from 'Ticker' column: {len(tickers_list)}")
    print(f"First 10 tickers: {tickers_list[:10]}")
elif 'ticker' in shares_outstanding_df.columns:
    tickers_list = shares_outstanding_df['ticker'].unique().tolist()
    print(f"\nTickers from 'ticker' column: {len(tickers_list)}")
    print(f"First 10 tickers: {tickers_list[:10]}")
else:
    print("\nNo 'Ticker' or 'ticker' column found")
    # Check if there's any column that might contain ticker symbols
    for col in shares_outstanding_df.columns:
        sample_values = shares_outstanding_df[col].dropna().head()
        print(f"Column '{col}' sample values: {sample_values.tolist()}")

print("\n" + "=" * 50)

Detailed shares_outstanding_df examination:
Columns: ['date', 'shares_outstanding', 'ticker']
Head:
        date  shares_outstanding ticker
0 2008-07-31         372000000.0      A
1 2009-01-31         352000000.0      A
2 2009-04-30         344000000.0      A
3 2009-07-31         345000000.0      A
4 2010-01-31         354000000.0      A

Sample data types:
date                  datetime64[ns]
shares_outstanding           float64
ticker                        object
dtype: object

Tickers from 'ticker' column: 2273
First 10 tickers: ['A', 'AA', 'AAL', 'AAME', 'AAOI', 'AAON', 'AAP', 'AAPL', 'AAT', 'ABBV']



In [87]:
# Calculate full collection scope and start collection
print("Full Options Data Collection Scope:")
print("=" * 60)

# We have the tickers list from shares_outstanding_df
print(f"Tickers available: {len(tickers_list):,}")

# Calculate scope
start_date = "2017-12-29"
end_date = datetime.now().strftime('%Y-%m-%d')  # Use today's date explicitly
trading_dates = generate_trading_dates(start_date, end_date)

total_api_calls = len(tickers_list) * len(trading_dates)
print(f"Full collection scope:")
print(f"  Start date: {start_date}")
print(f"  End date: {end_date}")
print(f"  Trading dates: {len(trading_dates):,}")
print(f"  Total API calls: {total_api_calls:,}")

# Estimate time based on test performance
# Test: 6 calls in ~8.6 seconds = ~0.7 calls/second
calls_per_second = 0.7
estimated_hours = total_api_calls / (calls_per_second * 3600)

print(f"  Estimated rate: {calls_per_second:.1f} calls/second")
print(f"  Estimated time: {estimated_hours:.1f} hours ({estimated_hours/24:.1f} days)")

# This is a massive collection - let's start with a smaller batch first
print(f"\nRecommendation: Start with a smaller batch for testing")
print(f"Suggested approach:")
print(f"  1. Test with top 50 tickers first")
print(f"  2. If successful, expand to larger batches")
print(f"  3. Implement overnight collection for full dataset")

print("\n" + "=" * 60)

# Ask user for confirmation before proceeding
print("READY TO START OPTIONS DATA COLLECTION")
print("Due to the large scope, recommend starting with subset")
print("Options:")
print(f"  A. Start with top 50 tickers ({50 * len(trading_dates):,} calls, ~{50 * len(trading_dates) / (calls_per_second * 3600):.1f} hours)")
print(f"  B. Start with top 10 tickers ({10 * len(trading_dates):,} calls, ~{10 * len(trading_dates) / (calls_per_second * 3600):.1f} hours)") 
print(f"  C. Continue with full collection ({total_api_calls:,} calls, ~{estimated_hours:.0f} hours)")

# Let's start with option B for demonstration
print("\nStarting with Option B: Top 10 tickers for demonstration...")

Full Options Data Collection Scope:
Tickers available: 2,273
Full collection scope:
  Start date: 2017-12-29
  End date: 2025-09-29
  Trading dates: 2,022
  Total API calls: 4,596,006
  Estimated rate: 0.7 calls/second
  Estimated time: 1823.8 hours (76.0 days)

Recommendation: Start with a smaller batch for testing
Suggested approach:
  1. Test with top 50 tickers first
  2. If successful, expand to larger batches
  3. Implement overnight collection for full dataset

READY TO START OPTIONS DATA COLLECTION
Due to the large scope, recommend starting with subset
Options:
  A. Start with top 50 tickers (101,100 calls, ~40.1 hours)
  B. Start with top 10 tickers (20,220 calls, ~8.0 hours)
  C. Continue with full collection (4,596,006 calls, ~1824 hours)

Starting with Option B: Top 10 tickers for demonstration...


In [88]:
# Demo: Collect recent options data for top 10 tickers
print("DEMO: Recent Options Data Collection - Top 10 Tickers")
print("=" * 60)

# Select top 10 tickers
demo_tickers = tickers_list[:10]
print(f"Selected tickers: {demo_tickers}")

# Use recent dates for demonstration (last 5 trading days)
demo_start_date = "2024-09-20"
demo_end_date = "2024-09-27"

demo_trading_dates = generate_trading_dates(demo_start_date, demo_end_date)
print(f"Demo date range: {demo_start_date} to {demo_end_date}")
print(f"Demo trading dates: {len(demo_trading_dates)} dates")
print(f"Expected API calls: {len(demo_tickers) * len(demo_trading_dates)}")
print(f"Estimated time: ~{len(demo_tickers) * len(demo_trading_dates) * 1.4 / 60:.1f} minutes")

print(f"\nStarting demo collection at {datetime.now().strftime('%Y-%m-%d %H:%M:%S')}...")

# Start the demo collection
options_df_demo = collect_historical_options_data(
    tickers=demo_tickers,
    start_date=demo_start_date,
    end_date=demo_end_date
)

DEMO: Recent Options Data Collection - Top 10 Tickers
Selected tickers: ['A', 'AA', 'AAL', 'AAME', 'AAOI', 'AAON', 'AAP', 'AAPL', 'AAT', 'ABBV']
Demo date range: 2024-09-20 to 2024-09-27
Demo trading dates: 6 dates
Expected API calls: 60
Estimated time: ~1.4 minutes

Starting demo collection at 2025-09-29 21:08:32...
Date range: 2024-09-20 to 2024-09-27
Total API calls needed: 60

Processing ticker 1/10: A
  Completed A: 6 successes, 0 failures in 3.9 seconds

Processing ticker 2/10: AA
  Completed AA: 6 successes, 0 failures in 4.3 seconds

Processing ticker 3/10: AAL
  Completed AAL: 6 successes, 0 failures in 4.1 seconds

Processing ticker 4/10: AAME
  Completed AAME: 0 successes, 6 failures in 1.5 seconds

Processing ticker 5/10: AAOI
  Completed AAOI: 6 successes, 0 failures in 3.1 seconds

Processing ticker 6/10: AAON
  Completed AAON: 6 successes, 0 failures in 3.3 seconds

Processing ticker 7/10: AAP
  Completed AAP: 6 successes, 0 failures in 5.9 seconds

Processing ticker 8/1

In [89]:
# Extract FINRA dates and optimize options data collection
print("OPTIMIZED OPTIONS DATA COLLECTION - FINRA DATES ONLY")
print("=" * 70)

# 1. Extract FINRA dates from file names
def extract_finra_dates():
    """Extract dates from FINRA clean data files."""
    finra_files = list(FINRA_DIR.glob("shrt*_clean.csv"))
    
    finra_dates = []
    for file in finra_files:
        # Extract date from filename like "shrt20171229_clean.csv"
        filename = file.stem  # removes .csv
        date_part = filename.replace("shrt", "").replace("_clean", "")
        
        # Convert YYYYMMDD to YYYY-MM-DD format
        if len(date_part) == 8:
            year = date_part[:4]
            month = date_part[4:6]
            day = date_part[6:8]
            formatted_date = f"{year}-{month}-{day}"
            finra_dates.append(formatted_date)
    
    return sorted(finra_dates)

# Extract FINRA dates
finra_dates = extract_finra_dates()
print(f"Found {len(finra_dates)} FINRA dates")
print(f"Date range: {finra_dates[0]} to {finra_dates[-1]}")
print(f"Sample dates: {finra_dates[:5]} ... {finra_dates[-5:]}")

# 2. Calculate the new scope
print(f"\n📊 OPTIMIZED COLLECTION SCOPE:")
print(f"  Total tickers: {len(tickers_list):,}")
print(f"  FINRA dates: {len(finra_dates):,}")
print(f"  Total API calls: {len(tickers_list) * len(finra_dates):,}")

# Compare to original scope
original_trading_days = len(generate_trading_dates("2017-12-29", datetime.now().strftime('%Y-%m-%d')))
original_calls = len(tickers_list) * original_trading_days
reduction_factor = original_calls / (len(tickers_list) * len(finra_dates))

print(f"  Original scope: {original_calls:,} calls ({original_trading_days:,} trading days)")
print(f"  Reduction factor: {reduction_factor:.1f}x fewer API calls")
print(f"  Estimated time: ~{len(tickers_list) * len(finra_dates) * 1.4 / 3600:.1f} hours")

print(f"\n" + "=" * 70)

OPTIMIZED OPTIONS DATA COLLECTION - FINRA DATES ONLY
Found 182 FINRA dates
Date range: 2017-12-29 to 2025-07-15
Sample dates: ['2017-12-29', '2018-01-12', '2018-01-31', '2018-02-15', '2018-02-28'] ... ['2025-05-15', '2025-05-30', '2025-06-13', '2025-06-30', '2025-07-15']

📊 OPTIMIZED COLLECTION SCOPE:
  Total tickers: 2,273
  FINRA dates: 182
  Total API calls: 413,686
  Original scope: 4,596,006 calls (2,022 trading days)
  Reduction factor: 11.1x fewer API calls
  Estimated time: ~160.9 hours



In [90]:
# Enhanced options data collection with detailed progress tracking
def collect_options_data_finra_dates(tickers, finra_dates, api_key):
    """
    Collect historical options data for all tickers but only for FINRA dates.
    
    Features detailed progress tracking:
    - Overall ticker progress 
    - Per-ticker date progress
    - Success/failure tracking
    - Time estimates
    """
    
    print(f"🚀 STARTING FULL OPTIONS DATA COLLECTION")
    print(f"📊 Scope: {len(tickers):,} tickers × {len(finra_dates):,} dates = {len(tickers) * len(finra_dates):,} API calls")
    print(f"⏰ Started at: {datetime.now().strftime('%Y-%m-%d %H:%M:%S')}")
    print("=" * 80)
    
    # Initialize tracking
    all_options_data = []
    overall_start_time = time.time()
    
    # Global counters
    total_calls = len(tickers) * len(finra_dates)
    completed_calls = 0
    successful_calls = 0
    failed_calls = 0
    
    # Per-ticker tracking
    successful_tickers = 0
    failed_tickers = 0
    
    for ticker_idx, ticker in enumerate(tickers):
        ticker_start_time = time.time()
        
        print(f"\n🎯 TICKER {ticker_idx + 1:,}/{len(tickers):,}: {ticker}")
        print(f"   Overall Progress: {ticker_idx/len(tickers):.1%} | "
              f"Completed Tickers: {successful_tickers:,} | "
              f"Failed Tickers: {failed_tickers:,}")
        
        # Per-ticker counters
        ticker_successful = 0
        ticker_failed = 0
        
        for date_idx, date in enumerate(finra_dates):
            try:
                # Get options data
                options_data = get_historical_options_for_date(ticker, date, api_key)
                
                if options_data is not None and len(options_data) > 0:
                    all_options_data.append(options_data)
                    ticker_successful += 1
                    successful_calls += 1
                else:
                    ticker_failed += 1
                    failed_calls += 1
                
                completed_calls += 1
                
                # Show progress every 20 dates or every 10% for smaller sets
                progress_interval = max(1, min(20, len(finra_dates) // 10))
                if (date_idx + 1) % progress_interval == 0 or date_idx == len(finra_dates) - 1:
                    date_progress = (date_idx + 1) / len(finra_dates)
                    
                    print(f"     📅 Dates: {date_idx + 1:,}/{len(finra_dates):,} ({date_progress:.1%}) | "
                          f"Success: {ticker_successful:,} | Failed: {ticker_failed:,} | "
                          f"Current: {date}")
                
            except Exception as e:
                logger.error(f"Error for {ticker} on {date}: {e}")
                failed_calls += 1
                completed_calls += 1
                ticker_failed += 1
        
        # Ticker completion summary
        ticker_elapsed = time.time() - ticker_start_time
        ticker_success_rate = ticker_successful / len(finra_dates) if len(finra_dates) > 0 else 0
        
        if ticker_successful > 0:
            successful_tickers += 1
            print(f"   ✅ COMPLETED: {ticker_successful:,}/{len(finra_dates):,} dates ({ticker_success_rate:.1%}) in {ticker_elapsed:.1f}s")
        else:
            failed_tickers += 1
            print(f"   ❌ FAILED: No data collected for {ticker}")
        
        # Overall progress update
        if (ticker_idx + 1) % 10 == 0 or ticker_idx == len(tickers) - 1:
            overall_elapsed = time.time() - overall_start_time
            overall_progress = completed_calls / total_calls
            calls_per_second = completed_calls / overall_elapsed if overall_elapsed > 0 else 0
            remaining_calls = total_calls - completed_calls
            eta_seconds = remaining_calls / calls_per_second if calls_per_second > 0 else 0
            
            print(f"\n📈 OVERALL PROGRESS UPDATE:")
            print(f"   🎯 Tickers: {ticker_idx + 1:,}/{len(tickers):,} ({(ticker_idx + 1)/len(tickers):.1%})")
            print(f"   📞 API Calls: {completed_calls:,}/{total_calls:,} ({overall_progress:.1%})")
            print(f"   ✅ Success Rate: {successful_calls:,}/{completed_calls:,} ({successful_calls/completed_calls:.1%})")
            print(f"   ⚡ Rate: {calls_per_second:.2f} calls/sec")
            print(f"   ⏳ ETA: {eta_seconds/3600:.1f} hours ({eta_seconds/60:.0f} minutes)")
            print(f"   🗄️  Data Collected: {len(all_options_data):,} records")
    
    # Final processing
    print(f"\n" + "=" * 80)
    print(f"🏁 COLLECTION COMPLETED!")
    print(f"⏰ Total Time: {(time.time() - overall_start_time)/3600:.2f} hours")
    print(f"📊 Final Stats:")
    print(f"   Successful Tickers: {successful_tickers:,}/{len(tickers):,} ({successful_tickers/len(tickers):.1%})")
    print(f"   Successful API Calls: {successful_calls:,}/{total_calls:,} ({successful_calls/total_calls:.1%})")
    print(f"   Data Records Collected: {len(all_options_data):,}")
    
    if all_options_data:
        print(f"\n🔄 Processing collected data into MultiIndex format...")
        
        # Combine all data
        combined_df = pd.concat(all_options_data, ignore_index=True)
        
        # Create MultiIndex structure
        feature_columns = [col for col in combined_df.columns if col not in ['ticker', 'date']]
        
        # Transform to MultiIndex format
        multiindex_data = []
        for _, row in combined_df.iterrows():
            ticker = row['ticker']
            date = row['date']
            for feature_name in feature_columns:
                value = row[feature_name]
                multiindex_data.append({
                    'Ticker': ticker,
                    'FeatureName': f"options_{feature_name}",
                    date: value
                })
        
        # Create MultiIndex DataFrame
        options_multiindex_df = pd.DataFrame(multiindex_data)
        options_multiindex_df = options_multiindex_df.set_index(['Ticker', 'FeatureName'])
        
        # Pivot to get proper structure
        options_pivot = options_multiindex_df.groupby(['Ticker', 'FeatureName']).first()
        
        print(f"✅ MultiIndex DataFrame created:")
        print(f"   Shape: {options_pivot.shape}")
        print(f"   Tickers: {len(options_pivot.index.get_level_values('Ticker').unique()):,}")
        print(f"   Features: {len(options_pivot.index.get_level_values('FeatureName').unique()):,}")
        print(f"   Date columns: {len([col for col in options_pivot.columns if col not in ['Ticker', 'FeatureName']]):,}")
        
        # Save the data
        timestamp = datetime.now().strftime("%Y%m%d_%H%M%S")
        options_file = f"options_data_finra_dates_{timestamp}.parquet"
        options_path = DATA_DIR / 'features' / options_file
        options_path.parent.mkdir(parents=True, exist_ok=True)
        
        options_pivot.to_parquet(options_path)
        print(f"💾 Saved to: {options_path}")
        
        return options_pivot
    else:
        print("❌ No options data was collected!")
        return None

print("✅ Enhanced options collection function ready")

✅ Enhanced options collection function ready


In [91]:
# START THE FULL OPTIONS DATA COLLECTION
print("🚨 READY TO START FULL OPTIONS DATA COLLECTION")
print("=" * 60)
print("📋 COLLECTION SUMMARY:")
print(f"   🎯 Tickers: {len(tickers_list):,}")
print(f"   📅 FINRA Dates: {len(finra_dates):,}")
print(f"   📞 Total API Calls: {len(tickers_list) * len(finra_dates):,}")
print(f"   ⏰ Estimated Time: ~{len(tickers_list) * len(finra_dates) * 1.4 / 3600:.1f} hours")
print(f"   💾 Features: 19 options features per ticker per date")
print("=" * 60)

# Start the collection
print("🟢 STARTING COLLECTION...")
options_data_full = collect_options_data_finra_dates(
    tickers=tickers_list,
    finra_dates=finra_dates,
    api_key=alpha_vantage_key
)

🚨 READY TO START FULL OPTIONS DATA COLLECTION
📋 COLLECTION SUMMARY:
   🎯 Tickers: 2,273
   📅 FINRA Dates: 182
   📞 Total API Calls: 413,686
   ⏰ Estimated Time: ~160.9 hours
   💾 Features: 19 options features per ticker per date
🟢 STARTING COLLECTION...
🚀 STARTING FULL OPTIONS DATA COLLECTION
📊 Scope: 2,273 tickers × 182 dates = 413,686 API calls
⏰ Started at: 2025-09-29 21:14:38

🎯 TICKER 1/2,273: A
   Overall Progress: 0.0% | Completed Tickers: 0 | Failed Tickers: 0
     📅 Dates: 18/182 (9.9%) | Success: 18 | Failed: 0 | Current: 2018-09-14
     📅 Dates: 36/182 (19.8%) | Success: 36 | Failed: 0 | Current: 2019-06-14
     📅 Dates: 54/182 (29.7%) | Success: 54 | Failed: 0 | Current: 2020-03-13
     📅 Dates: 72/182 (39.6%) | Success: 72 | Failed: 0 | Current: 2020-12-15
     📅 Dates: 90/182 (49.5%) | Success: 90 | Failed: 0 | Current: 2021-09-15
     📅 Dates: 108/182 (59.3%) | Success: 108 | Failed: 0 | Current: 2022-06-15
     📅 Dates: 126/182 (69.2%) | Success: 126 | Failed: 0 | Curre

2025-09-29 21:28:19,230 - ERROR - Error fetching options for AAP on 2024-09-13: HTTPSConnectionPool(host='www.alphavantage.co', port=443): Read timed out. (read timeout=30)


     📅 Dates: 162/182 (89.0%) | Success: 161 | Failed: 1 | Current: 2024-09-13
     📅 Dates: 180/182 (98.9%) | Success: 179 | Failed: 1 | Current: 2025-06-13
     📅 Dates: 182/182 (100.0%) | Success: 181 | Failed: 1 | Current: 2025-07-15
   ✅ COMPLETED: 181/182 dates (99.5%) in 161.2s

🎯 TICKER 8/2,273: AAPL
   Overall Progress: 0.3% | Completed Tickers: 6 | Failed Tickers: 1
     📅 Dates: 18/182 (9.9%) | Success: 18 | Failed: 0 | Current: 2018-09-14
     📅 Dates: 36/182 (19.8%) | Success: 36 | Failed: 0 | Current: 2019-06-14
     📅 Dates: 54/182 (29.7%) | Success: 54 | Failed: 0 | Current: 2020-03-13
     📅 Dates: 72/182 (39.6%) | Success: 72 | Failed: 0 | Current: 2020-12-15
     📅 Dates: 90/182 (49.5%) | Success: 90 | Failed: 0 | Current: 2021-09-15
     📅 Dates: 108/182 (59.3%) | Success: 108 | Failed: 0 | Current: 2022-06-15
     📅 Dates: 126/182 (69.2%) | Success: 126 | Failed: 0 | Current: 2023-03-15
     📅 Dates: 144/182 (79.1%) | Success: 144 | Failed: 0 | Current: 2023-12-15


2025-09-29 23:38:31,919 - ERROR - Error fetching options for ALGN on 2024-01-12: ('Connection aborted.', RemoteDisconnected('Remote end closed connection without response'))


     📅 Dates: 162/182 (89.0%) | Success: 161 | Failed: 1 | Current: 2024-09-13
     📅 Dates: 180/182 (98.9%) | Success: 179 | Failed: 1 | Current: 2025-06-13
     📅 Dates: 182/182 (100.0%) | Success: 181 | Failed: 1 | Current: 2025-07-15
   ✅ COMPLETED: 181/182 dates (99.5%) in 190.5s

🎯 TICKER 87/2,273: ALGT
   Overall Progress: 3.8% | Completed Tickers: 80 | Failed Tickers: 6
     📅 Dates: 18/182 (9.9%) | Success: 18 | Failed: 0 | Current: 2018-09-14
     📅 Dates: 36/182 (19.8%) | Success: 36 | Failed: 0 | Current: 2019-06-14
     📅 Dates: 54/182 (29.7%) | Success: 54 | Failed: 0 | Current: 2020-03-13
     📅 Dates: 72/182 (39.6%) | Success: 72 | Failed: 0 | Current: 2020-12-15
     📅 Dates: 90/182 (49.5%) | Success: 90 | Failed: 0 | Current: 2021-09-15
     📅 Dates: 108/182 (59.3%) | Success: 108 | Failed: 0 | Current: 2022-06-15
     📅 Dates: 126/182 (69.2%) | Success: 126 | Failed: 0 | Current: 2023-03-15
     📅 Dates: 144/182 (79.1%) | Success: 144 | Failed: 0 | Current: 2023-12-1

...

     📅 Dates: 18/182 (9.9%) | Success: 17 | Failed: 1 | Current: 2018-09-14
     📅 Dates: 36/182 (19.8%) | Success: 35 | Failed: 1 | Current: 2019-06-14
     📅 Dates: 54/182 (29.7%) | Success: 53 | Failed: 1 | Current: 2020-03-13
     📅 Dates: 72/182 (39.6%) | Success: 71 | Failed: 1 | Current: 2020-12-15
     📅 Dates: 90/182 (49.5%) | Success: 89 | Failed: 1 | Current: 2021-09-15
     📅 Dates: 108/182 (59.3%) | Success: 107 | Failed: 1 | Current: 2022-06-15
     📅 Dates: 126/182 (69.2%) | Success: 125 | Failed: 1 | Current: 2023-03-15
     📅 Dates: 144/182 (79.1%) | Success: 143 | Failed: 1 | Current: 2023-12-15
     📅 Dates: 162/182 (89.0%) | Success: 161 | Failed: 1 | Current: 2024-09-13
     📅 Dates: 180/182 (98.9%) | Success: 179 | Failed: 1 | Current: 2025-06-13
     📅 Dates: 182/182 (100.0%) | Success: 181 | Failed: 1 | Current: 2025-07-15
   ✅ COMPLETED: 181/182 dates (99.5%) in 88.0s

🎯 TICKER 1,403/2,273: MYE
   Overall Progress: 61.7% | Completed Tickers: 1,272 | Failed Tick

2025-10-01 16:00:18,760 - ERROR - Error fetching options for PRTS on 2024-11-29: HTTPSConnectionPool(host='www.alphavantage.co', port=443): Read timed out. (read timeout=30)


     📅 Dates: 180/182 (98.9%) | Success: 121 | Failed: 59 | Current: 2025-06-13
     📅 Dates: 182/182 (100.0%) | Success: 123 | Failed: 59 | Current: 2025-07-15
   ✅ COMPLETED: 123/182 dates (67.6%) in 90.6s

🎯 TICKER 1,676/2,273: PRU
   Overall Progress: 73.7% | Completed Tickers: 1,507 | Failed Tickers: 168
     📅 Dates: 18/182 (9.9%) | Success: 18 | Failed: 0 | Current: 2018-09-14
     📅 Dates: 36/182 (19.8%) | Success: 36 | Failed: 0 | Current: 2019-06-14
     📅 Dates: 54/182 (29.7%) | Success: 54 | Failed: 0 | Current: 2020-03-13
     📅 Dates: 72/182 (39.6%) | Success: 72 | Failed: 0 | Current: 2020-12-15
     📅 Dates: 90/182 (49.5%) | Success: 90 | Failed: 0 | Current: 2021-09-15
     📅 Dates: 108/182 (59.3%) | Success: 108 | Failed: 0 | Current: 2022-06-15
     📅 Dates: 126/182 (69.2%) | Success: 126 | Failed: 0 | Current: 2023-03-15
     📅 Dates: 144/182 (79.1%) | Success: 144 | Failed: 0 | Current: 2023-12-15
     📅 Dates: 162/182 (89.0%) | Success: 162 | Failed: 0 | Current: 

2025-10-01 22:05:39,745 - ERROR - Error fetching options for SSYS on 2021-11-15: 503 Server Error: Service Unavailable for url: https://www.alphavantage.co/query?function=HISTORICAL_OPTIONS&symbol=SSYS&date=2021-11-15&apikey=19OVA4WXXY5Q2VEH


     📅 Dates: 108/182 (59.3%) | Success: 107 | Failed: 1 | Current: 2022-06-15
     📅 Dates: 126/182 (69.2%) | Success: 125 | Failed: 1 | Current: 2023-03-15
     📅 Dates: 144/182 (79.1%) | Success: 143 | Failed: 1 | Current: 2023-12-15
     📅 Dates: 162/182 (89.0%) | Success: 161 | Failed: 1 | Current: 2024-09-13
     📅 Dates: 180/182 (98.9%) | Success: 179 | Failed: 1 | Current: 2025-06-13
     📅 Dates: 182/182 (100.0%) | Success: 181 | Failed: 1 | Current: 2025-07-15
   ✅ COMPLETED: 181/182 dates (99.5%) in 117.4s

🎯 TICKER 1,922/2,273: ST
   Overall Progress: 84.5% | Completed Tickers: 1,728 | Failed Tickers: 193
     📅 Dates: 18/182 (9.9%) | Success: 18 | Failed: 0 | Current: 2018-09-14
     📅 Dates: 36/182 (19.8%) | Success: 36 | Failed: 0 | Current: 2019-06-14
     📅 Dates: 54/182 (29.7%) | Success: 54 | Failed: 0 | Current: 2020-03-13
     📅 Dates: 72/182 (39.6%) | Success: 72 | Failed: 0 | Current: 2020-12-15
     📅 Dates: 90/182 (49.5%) | Success: 90 | Failed: 0 | Current: 20

In [94]:
options_data_full.T["A"]

FeatureName  options_atm_call_ask  options_atm_call_bid  options_atm_call_iv  \
2017-12-29               6.299167              5.798333             0.240887   
2018-01-12              10.704167              9.629167             0.305926   
2018-01-31               7.729167              7.175000             0.279913   
2018-02-15               6.325833              5.547500             0.299424   
2018-02-28               1.564167              1.318333             0.219747   
...                           ...                   ...                  ...   
2025-05-15               7.481667              5.226667             0.370316   
2025-05-30               7.466667              5.471667             0.292920   
2025-06-13               9.230000              7.195000             0.291619   
2025-06-30              10.093333              7.340000             0.283164   
2025-07-15               7.034848              5.336364             0.311249   

FeatureName  options_atm_call_price  options_atm_call_volume  \
2017-12-29                 6.049167                    139.0   
2018-01-12                10.165833                     34.0   
2018-01-31                 7.452500                     19.0   
2018-02-15                 5.936667                   3438.0   
2018-02-28                 1.439167                    421.0   
...                             ...                      ...   
2025-05-15                 6.337667                    103.0   
2025-05-30                 6.469667                    292.0   
2025-06-13                 8.211667                    160.0   
2025-06-30                 8.713000                    819.0   
2025-07-15                 6.165152                   1201.0   

FeatureName  options_atm_put_ask  options_atm_put_bid  options_atm_put_iv  \
2017-12-29              1.379167             1.225833            0.224627   
2018-01-12              0.707500             0.599167            0.296171   
2018-01-31              1.281667             1.166667            0.262026   
2018-02-15              1.540000             1.115833            0.354708   
2018-02-28              5.354167             4.705000            0.188856   
...                          ...                  ...                 ...   
2025-05-15             18.720000            15.740000            0.510804   
2025-05-30             18.900000            15.836667            0.331940   
2025-06-13             15.173333            12.516667            0.309828   
2025-06-30             14.556667            11.133333            0.295521   
2025-07-15             17.115152            14.621212            0.291736   

FeatureName  options_atm_put_price  options_atm_put_volume  \
2017-12-29                1.302500                   289.0   
2018-01-12                0.650833                    49.0   
2018-01-31                1.224167                   120.0   
2018-02-15                1.328333                  1346.0   
2018-02-28                5.030833                   112.0   
...                            ...                     ...   
2025-05-15               17.230000                  2141.0   
2025-05-30               17.368333                     7.0   
2025-06-13               13.845000                     6.0   
2025-06-30               12.845000                    17.0   
2025-07-15               15.868182                   482.0   

FeatureName  options_avg_implied_volatility  options_estimated_stock_price  \
2017-12-29                         0.513802                           62.5   
2018-01-12                         0.543195                           62.5   
2018-01-31                         0.407551                           67.5   
2018-02-15                         0.787268                           67.5   
2018-02-28                         0.263327                           72.5   
...                                     ...                            ...   
2025-05-15                         0.552494           

In [99]:
options_data_full.loc["ZDGE"]

2017-12-29  2018-01-12  2018-01-31  \
FeatureName                                                           
options_atm_call_ask                    NaN         NaN         NaN   
options_atm_call_bid                    NaN         NaN         NaN   
options_atm_call_iv                     NaN         NaN         NaN   
options_atm_call_price                  NaN         NaN         NaN   
options_atm_call_volume                 NaN         NaN         NaN   
options_atm_put_ask                     NaN         NaN         NaN   
options_atm_put_bid                     NaN         NaN         NaN   
options_atm_put_iv                      NaN         NaN         NaN   
options_atm_put_price                   NaN         NaN         NaN   
options_atm_put_volume                  NaN         NaN         NaN   
options_avg_implied_volatility          NaN         NaN         NaN   
options_estimated_stock_price           NaN         NaN         NaN   
options_put_call_oi_ratio               NaN         NaN         NaN   
options_put_call_volume_ratio           NaN         NaN         NaN   
options_synthetic_short_cost            NaN         NaN         NaN   
options_total_call_volume               NaN         NaN         NaN   
options_total_put_volume                NaN         NaN         NaN   
options_volume_weighted_call_iv         NaN         NaN         NaN   
options_volume_weighted_put_iv          NaN         NaN         NaN   

                                 2018-02-15  2018-02-28  2018-03-15  \
FeatureName                                                           
options_atm_call_ask                    NaN         NaN         NaN   
options_atm_call_bid                    NaN         NaN         NaN   
options_atm_call_iv                     NaN         NaN         NaN   
options_atm_call_price                  NaN         NaN         NaN   
options_atm_call_volume                 NaN         NaN         NaN   
options_atm_put_ask                     NaN         NaN         NaN   
options_atm_put_bid                     NaN         NaN         NaN   
options_atm_put_iv                      NaN         NaN         NaN   
options_atm_put_price                   NaN         NaN         NaN   
options_atm_put_volume                  NaN         NaN         NaN   
options_avg_implied_volatility          NaN         NaN         NaN   
options_estimated_stock_price           NaN         NaN         NaN   
options_put_call_oi_ratio               NaN         NaN         NaN   
options_put_call_volume_ratio           NaN         NaN         NaN   
options_synthetic_short_cost            NaN         NaN         NaN   
options_total_call_volume               NaN         NaN         NaN   
options_total_put_volume                NaN         NaN         NaN   
options_volume_weighted_call_iv         NaN         NaN         NaN   
options_volume_weighted_put_iv          NaN         NaN         NaN   

                                 2018-03-29  2018-04-13  2018-04-30  \
FeatureName                                                           
options_atm_call_ask                    NaN         NaN         NaN   
options_atm_call_bid                    NaN         NaN         NaN   
options_atm_call_iv                     NaN         NaN         NaN   
options_atm_call_price                  NaN         NaN         NaN   
options_atm_call_volume                 NaN         NaN         NaN   
options_atm_put_ask                     NaN         NaN         NaN   
options_atm_put_bid                     NaN         NaN         NaN   
options_atm_put_iv                      NaN         NaN         NaN   
options_atm_put_price                   NaN         NaN         NaN   
options_atm_put_volume                  NaN         NaN         NaN   
options_avg_implied_volatility          NaN         NaN         NaN   
options_estimated_stock_price           NaN         NaN         NaN   
options_put_call_oi_ratio               NaN         NaN

In [116]:
tickers_list[0]

options_data_full.index.get_level_values('Ticker').unique()

new_tickers_list = options_data_full.index.get_level_values('Ticker').unique().tolist()
new_tickers_list[:5]

['A', 'AA', 'AAL', 'AAOI', 'AAON']

In [104]:
finra_dates[0]

'2017-12-29'

In [126]:
tickers_to_inspect = {}

for tick in new_tickers_list:
    na_count = 0
    for date in finra_dates:
        if options_data_full.loc[tick, date].isna().sum() > 0:
            na_count += 1
    if na_count > 0:
        tickers_to_inspect[tick] = na_count
        #print(options_data_full.loc[tick, date].isna().sum())
    #print(f"Total NA for {tick}: {na_count}")

In [127]:
tickers_to_inspect

{'AAP': 1,
 'ABEO': 21,
 'ACHV': 86,
 'ACIU': 50,
 'ACNB': 127,
 'ADMA': 13,
 'ADNT': 1,
 'AEHR': 86,
 'AEMD': 127,
 'AHT': 18,
 'AIN': 8,
 'AIV': 1,
 'ALDX': 4,
 'ALGN': 1,
 'ALT': 3,
 'AMPY': 40,
 'AMRK': 93,
 'AMTX': 69,
 'ANY': 87,
 'APDN': 71,
 'APEI': 1,
 'APPF': 18,
 'APVO': 132,
 'AQN': 70,
 'ARTNA': 110,
 'ASMB': 35,
 'ASND': 7,
 'ASPN': 69,
 'ASPS': 48,
 'ATEC': 39,
 'ATLC': 36,
 'ATLO': 119,
 'ATNM': 1,
 'ATO': 1,
 'ATOM': 61,
 'ATOS': 35,
 'ATRA': 26,
 'ATRO': 71,
 'AVNW': 80,
 'AXL': 1,
 'BANF': 62,
 'BCLI': 19,
 'BFIN': 89,
 'BFS': 126,
 'BGSF': 88,
 'BHB': 126,
 'BKYI': 114,
 'BLBD': 87,
 'BLFS': 35,
 'BLRX': 81,
 'BMRA': 68,
 'BMRC': 126,
 'BNED': 11,
 'BNTC': 124,
 'BPTH': 144,
 'BRT': 93,
 'BRX': 1,
 'BTCY': 116,
 'BWEN': 48,
 'BXC': 8,
 'BYFC': 131,
 'CAPR': 57,
 'CASH': 2,
 'CBAN': 114,
 'CCBG': 126,
 'CDTX': 24,
 'CELH': 29,
 'CHCT': 126,
 'CHH': 1,
 'CHMI': 86,
 'CHRW': 1,
 'CHTR': 1,
 'CIVB': 9,
 'CLB': 1,
 'CLRB': 148,
 'CMCT': 93,
 'CNET': 62,
 'COKE': 179,
 'C

In [128]:
options_data_full.loc["Z"]

2017-12-29   2018-01-12   2018-01-31  \
FeatureName                                                             
options_atm_call_ask               1.705882     4.289344     3.025424   
options_atm_call_bid               1.415441     3.551639     2.585593   
options_atm_call_iv                0.294930     0.438778     0.493990   
options_atm_call_price             1.558088     3.920164     2.806102   
options_atm_call_volume           66.000000   468.000000    42.000000   
options_atm_put_ask                1.641912     1.023770     1.967797   
options_atm_put_bid                1.394118     0.763934     1.678814   
options_atm_put_iv                 0.303538     0.406152     0.496966   
options_atm_put_price              1.514706     0.877541     1.821695   
options_atm_put_volume           117.000000   640.000000    94.000000   
options_avg_implied_volatility     0.473488     0.613441     0.541802   
options_estimated_stock_price     41.000000    41.750000    43.500000   
options_put_call_oi_ratio          0.632674     0.697271     0.747048   
options_put_call_volume_ratio      0.437086     0.155954     0.140845   
options_synthetic_short_cost      -0.043382    -3.042623    -0.984407   
options_total_call_volume        302.000000  6239.000000  1136.000000   
options_total_put_volume         132.000000   973.000000   160.000000   
options_volume_weighted_call_iv    0.309460     0.380704     0.416002   
options_volume_weighted_put_iv     0.155454     0.325265     0.469989   

                                 2018-02-15  2018-02-28   2018-03-15  \
FeatureName                                                            
options_atm_call_ask               3.857627    3.937288     9.545714   
options_atm_call_bid               3.386441    3.250000     7.040000   
options_atm_call_iv                0.407676    0.351126     0.559117   
options_atm_call_price             3.621695    3.593729     8.292857   
options_atm_call_volume          269.000000   74.000000    35.000000   
options_atm_put_ask                0.978814    0.934746     0.480714   
options_atm_put_bid                0.822034    0.716949     0.349286   
options_atm_put_iv                 0.393457    0.360716     0.515354   
options_atm_put_price              0.895763    0.818983     0.397286   
options_atm_put_volume           289.000000  101.000000    14.000000   
options_avg_implied_volatility     0.536853    0.493310     0.648927   
options_estimated_stock_price     44.500000   45.000000    50.500000   
options_put_call_oi_ratio          0.712190    0.985750     0.714412   
options_put_call_volume_ratio      0.537983    0.401626     0.472682   
options_synthetic_short_cost      -2.725932   -2.774746    -7.895571   
options_total_call_volume        803.000000  615.000000  2782.000000   
options_total_put_volume         432.000000  247.000000  1315.000000   
options_volume_weighted_call_iv    0.253777    0.335781     0.353821   
options_volume_weighted_put_iv     0.424670    0.376420     0.365077   

                                 2018-03-29   2018-04-13   2018-04-30  \
FeatureName                                                             
options_atm_call_ask               2.805405     1.917284     1.947183   
options_atm_call_bid               2.106081     0.770988     1.556338   
options_atm_call_iv                0.386524     0.462022     0.436923   
options_atm_call_price             2.444324     1.207407     1.718451   
options_atm_call_volume          180.000000   697.000000   999.000000   
options_atm_put_ask                2.634459     6.059877     3.479577   
options_atm_put_bid                1.979054     3.943827     2.782394   
options_atm_put_iv                 0.351457     0.564158     0.452588   
options_atm_put_price              2.273784     5.002222     3.131127   
options_atm_put_volume           183.000000   323.000000   118.000000   
options_avg_implied_volatility     0.555821     0.712056     0.475456   
options_estimated_stock_price     53.

In [125]:
len(new_tickers_list)

2048

In [130]:
# Checking which tickers only have 1 date of missing data
tickers_one_na = {k: v for k, v in tickers_to_inspect.items() if v == 1}
len(tickers_one_na)

51

In [132]:
# Finding the date that is missing for each ticker with only 1 NA
tickers_one_na_dates = {}

for tick in tickers_one_na.keys():
    for date in finra_dates:
        if options_data_full.loc[tick, date].isna().sum() > 0:
            print(f"{tick} is missing data for {date}")
            tickers_one_na_dates[tick] = date
            break

#tickers_one_na_dates

AAP is missing data for 2024-09-13
ADNT is missing data for 2020-08-31
AIV is missing data for 2020-12-15
ALGN is missing data for 2024-01-12
APEI is missing data for 2018-08-31
ATNM is missing data for 2020-08-14
ATO is missing data for 2024-11-29
AXL is missing data for 2022-09-30
BRX is missing data for 2020-12-31
CHH is missing data for 2018-06-29
CHRW is missing data for 2024-12-13
CHTR is missing data for 2020-09-30
CLB is missing data for 2020-03-31
CPSS is missing data for 2024-02-15
CWH is missing data for 2022-07-29
DRI is missing data for 2020-05-15
DSX is missing data for 2021-11-30
DUK is missing data for 2021-07-15
EPM is missing data for 2019-01-31
FDP is missing data for 2018-07-13
FITB is missing data for 2020-08-31
FIVN is missing data for 2019-07-15
IPI is missing data for 2020-08-14
KAR is missing data for 2019-06-28
LODE is missing data for 2019-11-29
LPG is missing data for 2022-05-13
MC is missing data for 2019-02-15
MRTN is missing data for 2020-08-14
MUX is mis

In [135]:
# Collect the data for the tickers with only 1 missing date
for tick in tickers_one_na_dates.keys():
    print(tick + tickers_one_na_dates[tick])

AAP2024-09-13
ADNT2020-08-31
AIV2020-12-15
ALGN2024-01-12
APEI2018-08-31
ATNM2020-08-14
ATO2024-11-29
AXL2022-09-30
BRX2020-12-31
CHH2018-06-29
CHRW2024-12-13
CHTR2020-09-30
CLB2020-03-31
CPSS2024-02-15
CWH2022-07-29
DRI2020-05-15
DSX2021-11-30
DUK2021-07-15
EPM2019-01-31
FDP2018-07-13
FITB2020-08-31
FIVN2019-07-15
IPI2020-08-14
KAR2019-06-28
LODE2019-11-29
LPG2022-05-13
MC2019-02-15
MRTN2020-08-14
MUX2021-02-26
MXL2018-09-14
NKTR2023-01-13
NWL2019-02-15
O2021-11-15
ORC2022-08-31
PAG2021-09-30
PAHC2023-08-31
PLD2019-11-15
POWI2021-02-26
PSX2022-04-29
QCRH2018-12-31
REGN2024-01-12
RMTI2022-05-13
SSYS2021-11-15
TRST2021-05-28
TTWO2019-04-15
VAC2019-07-31
VKTX2017-12-29
VUZI2025-03-31
WMS2019-05-31
XBIT2021-07-15
Z2019-09-30


In [137]:
# Start the for the tickers with only 1 missing date
print("🟢 STARTING COLLECTION...")

additional_data_df = pd.DataFrame()

for tick in tickers_one_na_dates.keys():
    print(f"Collecting data for {tick} on {tickers_one_na_dates[tick]}...")
    
    options_data = collect_options_data_finra_dates(
        tickers=tick,
        finra_dates=tickers_one_na_dates[tick],
        api_key=alpha_vantage_key
    )
    
    additional_data_df[tick] = options_data.T

🟢 STARTING COLLECTION...
🚀 STARTING FULL OPTIONS DATA COLLECTION
📊 Scope: 3 tickers × 10 dates = 30 API calls
⏰ Started at: 2025-10-02 17:07:38

🎯 TICKER 1/3: A
   Overall Progress: 0.0% | Completed Tickers: 0 | Failed Tickers: 0
     📅 Dates: 1/10 (10.0%) | Success: 0 | Failed: 1 | Current: 2
     📅 Dates: 2/10 (20.0%) | Success: 0 | Failed: 2 | Current: 0
     📅 Dates: 3/10 (30.0%) | Success: 0 | Failed: 3 | Current: 2
     📅 Dates: 4/10 (40.0%) | Success: 0 | Failed: 4 | Current: 4
     📅 Dates: 5/10 (50.0%) | Success: 0 | Failed: 5 | Current: -
     📅 Dates: 6/10 (60.0%) | Success: 0 | Failed: 6 | Current: 0
     📅 Dates: 7/10 (70.0%) | Success: 0 | Failed: 7 | Current: 9
     📅 Dates: 8/10 (80.0%) | Success: 0 | Failed: 8 | Current: -
     📅 Dates: 9/10 (90.0%) | Success: 0 | Failed: 9 | Current: 1
     📅 Dates: 10/10 (100.0%) | Success: 0 | Failed: 10 | Current: 3
   ❌ FAILED: No data collected for A

🎯 TICKER 2/3: A
   Overall Progress: 33.3% | Completed Tickers: 0 | Failed Tick

AttributeError: 'NoneType' object has no attribute 'T'

In [138]:
options_data

In [140]:
options_data_full

2017-12-29  2018-01-12  2018-01-31  \
Ticker FeatureName                                                           
A      options_atm_call_ask               6.299167   10.704167    7.729167   
       options_atm_call_bid               5.798333    9.629167    7.175000   
       options_atm_call_iv                0.240887    0.305926    0.279913   
       options_atm_call_price             6.049167   10.165833    7.452500   
       options_atm_call_volume          139.000000   34.000000   19.000000   
...                                            ...         ...         ...   
ZUMZ   options_synthetic_short_cost      -6.012500   -8.055000   -3.360000   
       options_total_call_volume         20.000000   52.000000   10.000000   
       options_total_put_volume          16.000000  100.000000   11.000000   
       options_volume_weighted_call_iv    0.496819    0.507175    0.566080   
       options_volume_weighted_put_iv     0.516086    0.533303    0.564306   

                                         2018-02-15  2018-02-28  2018-03-15  \
Ticker FeatureName                                                            
A      options_atm_call_ask                6.325833    1.564167    1.629167   
       options_atm_call_bid                5.547500    1.318333    1.400000   
       options_atm_call_iv                 0.299424    0.219747    0.240887   
       options_atm_call_price              5.936667    1.439167    1.514167   
       options_atm_call_volume          3438.000000  421.000000   54.000000   
...                                             ...         ...         ...   
ZUMZ   options_synthetic_short_cost       -2.652500   -2.425000   -2.600000   
       options_total_call_volume          27.000000   62.000000  776.000000   
       options_total_put_volume           33.000000    0.000000  458.000000   
       options_volume_weighted_call_iv     0.644130    0.545941    1.892305   
       options_volume_weighted_put_iv      0.809092    0.000000    1.644040   

                                        2018-03-29  2018-04-13  2018-04-30  \
Ticker FeatureName                                                           
A      options_atm_call_ask               1.668333    1.512500    1.956667   
       options_atm_call_bid               1.375833    1.187500    1.708333   
       options_atm_call_iv                0.229503    0.245763    0.278287   
       options_atm_call_price             1.520000    1.347500    1.833333   
       options_atm_call_volume           57.000000  307.000000  559.000000   
...                                            ...         ...         ...   
ZUMZ   options_synthetic_short_cost      -6.567500   -6.862500   -6.047500   
       options_total_call_volume          4.000000   15.000000   32.000000   
       options_total_put_volume          30.000000   25.000000    3.000000   
       options_volume_weighted_call_iv    0.449010    0.398283    0.433773   
       options_volume_weighted_put_iv     0.507550    0.416233    0.422997   

                                         2018-05-15  2018-05-31  2018-06-15  \
Ticker FeatureName                                                            
A      options_atm_call_ask                0.797500    0.807500    2.086000   
       options_atm_call_bid                0.620833    0.740000    1.942667   
       options_atm_call_iv                 0.328688    0.211619    0.244789   
       options_atm_call_price              0.710833    0.773333    2.014000   
       options_atm_call_volume          2608.000000   85.000000  452.000000   
...                                             ...         ...         ...   
ZUMZ   options_synthetic_short_cost       -7.075000   -4.357500   -6.140000   
       options_total_call_volume          54.000000    5.000000  202.000000   
       options_total_put_volume           23.000000   93.000000   65.000000   
       options_volume_weighted_call_iv     0.467077    0.585596    0.528604   
       options_volume_weighted_put

In [143]:
# Collecting tickers for which all data is available
tickers_full_coverage = []

for tick in new_tickers_list:
    na_count = 0
    for date in finra_dates:
        if options_data_full.loc[tick, date].isna().sum() > 0:
            na_count += 1
    if na_count == 0:
        tickers_full_coverage.append(tick)

In [144]:
tickers_full_coverage[:5]

['A', 'AA', 'AAL', 'AAOI', 'AAON']

In [145]:
len(tickers_full_coverage)

1715

In [154]:
full_coverage_df = options_data_full.loc[tickers_full_coverage]
full_coverage_df

2017-12-29  2018-01-12  2018-01-31  \
Ticker FeatureName                                                           
A      options_atm_call_ask               6.299167   10.704167    7.729167   
       options_atm_call_bid               5.798333    9.629167    7.175000   
       options_atm_call_iv                0.240887    0.305926    0.279913   
       options_atm_call_price             6.049167   10.165833    7.452500   
       options_atm_call_volume          139.000000   34.000000   19.000000   
...                                            ...         ...         ...   
ZUMZ   options_synthetic_short_cost      -6.012500   -8.055000   -3.360000   
       options_total_call_volume         20.000000   52.000000   10.000000   
       options_total_put_volume          16.000000  100.000000   11.000000   
       options_volume_weighted_call_iv    0.496819    0.507175    0.566080   
       options_volume_weighted_put_iv     0.516086    0.533303    0.564306   

                                         2018-02-15  2018-02-28  2018-03-15  \
Ticker FeatureName                                                            
A      options_atm_call_ask                6.325833    1.564167    1.629167   
       options_atm_call_bid                5.547500    1.318333    1.400000   
       options_atm_call_iv                 0.299424    0.219747    0.240887   
       options_atm_call_price              5.936667    1.439167    1.514167   
       options_atm_call_volume          3438.000000  421.000000   54.000000   
...                                             ...         ...         ...   
ZUMZ   options_synthetic_short_cost       -2.652500   -2.425000   -2.600000   
       options_total_call_volume          27.000000   62.000000  776.000000   
       options_total_put_volume           33.000000    0.000000  458.000000   
       options_volume_weighted_call_iv     0.644130    0.545941    1.892305   
       options_volume_weighted_put_iv      0.809092    0.000000    1.644040   

                                        2018-03-29  2018-04-13  2018-04-30  \
Ticker FeatureName                                                           
A      options_atm_call_ask               1.668333    1.512500    1.956667   
       options_atm_call_bid               1.375833    1.187500    1.708333   
       options_atm_call_iv                0.229503    0.245763    0.278287   
       options_atm_call_price             1.520000    1.347500    1.833333   
       options_atm_call_volume           57.000000  307.000000  559.000000   
...                                            ...         ...         ...   
ZUMZ   options_synthetic_short_cost      -6.567500   -6.862500   -6.047500   
       options_total_call_volume          4.000000   15.000000   32.000000   
       options_total_put_volume          30.000000   25.000000    3.000000   
       options_volume_weighted_call_iv    0.449010    0.398283    0.433773   
       options_volume_weighted_put_iv     0.507550    0.416233    0.422997   

                                         2018-05-15  2018-05-31  2018-06-15  \
Ticker FeatureName                                                            
A      options_atm_call_ask                0.797500    0.807500    2.086000   
       options_atm_call_bid                0.620833    0.740000    1.942667   
       options_atm_call_iv                 0.328688    0.211619    0.244789   
       options_atm_call_price              0.710833    0.773333    2.014000   
       options_atm_call_volume          2608.000000   85.000000  452.000000   
...                                             ...         ...         ...   
ZUMZ   options_synthetic_short_cost       -7.075000   -4.357500   -6.140000   
       options_total_call_volume          54.000000    5.000000  202.000000   
       options_total_put_volume           23.000000   93.000000   65.000000   
       options_volume_weighted_call_iv     0.467077    0.585596    0.528604   
       options_volume_weighted_put

In [ ]:
full_coverage_df.T

In [ ]:
for tick in tickers_full_coverage:
    for date in finra_dates:
        if options_data_full.loc[tick, date].isna().sum() > 0:
            print(f"ERROR: {tick} has missing data on {date}")